<h1>Applied Data Science Capstone</h1>

<i>IBM Data Science Coursera Course</i>

<h2>Jupyter Notebook for Capstone Project</h2>
By Xander Mol

<h3>Week 4-5 Peer Graded Assignment</h3>

<h1>Searching for the optimal postal code to start a salad bar</h1>

Combine data from the Dutch Central Bureau of Statistics (CBS) per Dutch postal code on demographics and income with Foursquare data on venues in those areas to find an optimal spot to start a salad bar that is close to our target group of single females.

<h3>Environment preparation</h3>

In [1]:
# Installs
!conda install -c conda-forge geopy --yes #Geolocation library
!conda install -c conda-forge geocoder --yes #Geolocation library
!conda install -c conda-forge folium=0.5.0 --yes #Mapping library

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

In [2]:
# Imports
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from zipfile import ZipFile # library for handling ZIP files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder

import requests # library to handle requests
from requests import Request

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans

import folium # map rendering library
from folium import plugins

print('Libraries imported.')

Libraries imported.


### Download Dutch demographic data based on postal code

Dutch postal codes have 6 positions: four digits followed by two letters. The four digits are the best Dutch proxy of neighbourhoods.

The Dutch Central Bureau of Statistics has publised an Excel dataset of demographics per four digit postal code.

See https://www.cbs.nl/nl-nl/maatwerk/2016/51/bevolking-per-viercijferige-postcode-op-1-januari-2016

In [3]:
#Table of Dutch inhabitants per four digit postal code. Inhabitants split per age and sex, migration background and household composition.
#Excel has multi row header, so header is set to none. Columns BU and BV not imported as we do not need it
demo = pd.read_excel('https://www.cbs.nl/-/media/_excel/2016/51/bevolking-per-postcode-1-januari-2016.xls',
                     sheet_name = 'Bevolking per postcode', header = None, skiprows = 5, nrows = 4037, dtype = float, usecols = range(0, 72))
demo.columns = ['postcode', 'tot_inwoners',
                'tot_0-5', 'tot_5-10', 'tot_10-15', 'tot_15-20', 'tot_20-25', 'tot_25-30', 'tot_30-35', 'tot_35-40', 'tot_40-45', 'tot_45-50',
                'tot_50-55', 'tot_55-60', 'tot_60-65', 'tot_65-70', 'tot_70-75', 'tot_75-80', 'tot_80-85', 'tot_85-90', 'tot_90-95', 'tot_95-',
                'tot_man',
                'man_0-5', 'man_5-10', 'man_10-15', 'man_15-20', 'man_20-25', 'man_25-30', 'man_30-35', 'man_35-40', 'man_40-45', 'man_45-50',
                'man_50-55', 'man_55-60', 'man_60-65', 'man_65-70', 'man_70-75', 'man_75-80', 'man_80-85', 'man_85-90', 'man_90-95', 'man_95-',
                'tot_vrouw',
                'vrouw_0-5', 'vrouw_5-10', 'vrouw_10-15', 'vrouw_15-20', 'vrouw_20-25', 'vrouw_25-30', 'vrouw_30-35', 'vrouw_35-40', 'vrouw_40-45', 'vrouw_45-50',
                'vrouw_50-55', 'vrouw_55-60', 'vrouw_60-65', 'vrouw_65-70', 'vrouw_70-75', 'vrouw_75-80', 'vrouw_80-85', 'vrouw_85-90', 'vrouw_90-95', 'vrouw_95-',
                'tot_allochtoon', 'allochtoon_westers', 'allochtoon_nietwesters',
                'tot_huishoudens', 'eenspersoons', 'meer_zonder_kinderen', 'meer_met_kinderen',
                'gem_huish_grootte'               ]
demo['postcode'] = demo['postcode'].astype(int)
demo.head()

postcode  tot_inwoners  tot_0-5  tot_5-10  tot_10-15  tot_15-20  tot_20-25  \
0      1011        9605.0    295.0     290.0      220.0      315.0      885.0   
1      1012        8245.0    220.0     135.0      115.0      160.0     1100.0   
2      1013       21185.0   1110.0     855.0      675.0      690.0     1290.0   
3      1014         580.0     30.0      15.0        5.0       15.0       25.0   
4      1015       14860.0    575.0     465.0      430.0      445.0     1085.0   

   tot_25-30  tot_30-35  tot_35-40  tot_40-45  tot_45-50  tot_50-55  \
0     1100.0      835.0      650.0      615.0      650.0      770.0   
1     1705.0     1165.0      700.0      545.0      510.0      490.0   
2     2075.0     2145.0     1910.0     1670.0     1685.0     1630.0   
3      135.0      125.0       60.0       50.0       35.0       25.0   
4     1605.0     1445.0     1105.0     1075.0     1235.0     1175.0   

   tot_55-60  tot_60-65  tot_65-70  tot_70-75  tot_75-80  tot_80-85  \
0      785.0      750.0      670.0      360.0      200.0      115.0   
1      420.0      335.0      300.0      180.0       85.0       40.0   
2     1470.0     1335.0     1135.0      670.0      400.0      255.0   
3       25.0       15.0       10.0       10.0       10.0        5.0   
4     1025.0      925.0     1055.0      565.0      360.0      180.0   

   tot_85-90  tot_90-95  tot_95-  tot_man  man_0-5  man_5-10  man_10-15  \
0       60.0       35.0     15.0   4990.0    145.0     135.0      105.0   
1       15.0        5.0      0.0   4495.0    105.0      60.0       60.0   
2      120.0       50.0     15.0  10630.0    540.0     445.0      345.0   
3        0.0        0.0      0.0    335.0     15.0       5.0        0.0   
4       70.0       35.0      5.0   7530.0    285.0     230.0      220.0   

   man_15-20  man_20-25  man_25-30  man_30-35  man_35-40  man_40-45  \
0      150.0      370.0      515.0      440.0      380.0      355.0   
1       65.0      460.0      845.0      645.0      440.0      360.0   
2      355.0      585.0      950.0     1080.0      930.0      890.0   
3       10.0       15.0       75.0       70.0       35.0       35.0   
4      225.0      450.0      730.0      725.0      590.0      580.0   

   man_45-50  man_50-55  man_55-60  man_60-65  man_65-70  man_70-75  \
0      385.0      460.0      430.0      410.0      350.0      190.0   
1      315.0      335.0      270.0      195.0      170.0      105.0   
2      915.0      880.0      740.0      670.0      575.0      350.0   
3       20.0       20.0       20.0       10.0        5.0        5.0   
4      670.0      650.0      560.0      470.0      540.0      295.0   

   man_75-80  man_80-85  man_85-90  man_90-95  man_95-  tot_vrouw  vrouw_0-5  \
0      100.0       50.0       15.0       10.0      5.0     4615.0      150.0   
1       55.0       20.0        5.0        5.0      0.0     3745.0      120.0   
2      210.0      120.0       40.0       15.0      0.0    10555.0      570.0   
3        5.0        5.0        0.0        0.0      0.0      245.0       20.0   
4      185.0       75.0       25.0       10.0      5.0     7330.0      290.0   

   vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  vrouw_25-30  \
0       150.0        115.0        160.0        515.0        585.0   
1        75.0         65.0        100.0        645.0        865.0   
2       410.0        330.0        335.0        705.0       1125.0   
3        10.0          0.0          5.0         15.0         70.0   
4       230.0        205.0        225.0        635.0        875.0   

   vrouw_30-35  vrouw_35-40  vrouw_40-45  vrouw_45-50  vrouw_50-55  \
0        395.0        270.0        260.0        265.0        310.0   
1        525.0        260.0        185.0        185.0        160.0   
2       1065.0        980.0        780.0        770.0        745.0   
3         55.0         20.0         15.0         10.0          5.0   
4        720.0        515.0        500.0        565.0        520.0   

   vrouw_55-60  vrouw_60-65  vrouw_65-70

In [4]:
demo.shape

(4037, 72)

In [5]:
demo.dtypes

postcode                    int64
tot_inwoners              float64
tot_0-5                   float64
tot_5-10                  float64
tot_10-15                 float64
tot_15-20                 float64
tot_20-25                 float64
tot_25-30                 float64
tot_30-35                 float64
tot_35-40                 float64
tot_40-45                 float64
tot_45-50                 float64
tot_50-55                 float64
tot_55-60                 float64
tot_60-65                 float64
tot_65-70                 float64
tot_70-75                 float64
tot_75-80                 float64
tot_80-85                 float64
tot_85-90                 float64
tot_90-95                 float64
tot_95-                   float64
tot_man                   float64
man_0-5                   float64
man_5-10                  float64
man_10-15                 float64
man_15-20                 float64
man_20-25                 float64
man_25-30                 float64
man_30-35     

In [6]:
demo.describe()

postcode  tot_inwoners      tot_0-5     tot_5-10    tot_10-15  \
count  4037.000000   4037.000000  4037.000000  4037.000000  4037.000000   
mean   5675.431756   4205.483032   217.184791   230.355462   245.973495   
std    2671.752148   4198.150829   243.444008   252.998869   259.059261   
min    1011.000000      0.000000     0.000000     0.000000     0.000000   
25%    3332.000000    670.000000    30.000000    35.000000    40.000000   
50%    5711.000000   2665.000000   125.000000   135.000000   155.000000   
75%    8051.000000   6885.000000   345.000000   365.000000   380.000000   
max    9999.000000  28315.000000  2125.000000  2320.000000  2395.000000   

         tot_15-20    tot_20-25    tot_25-30    tot_30-35    tot_35-40  \
count  4037.000000  4037.000000  4037.000000  4037.000000  4037.000000   
mean    252.276443   264.036413   265.252663   252.012633   250.016101   
std     257.089459   359.385678   347.647781   307.972293   283.131502   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%      45.000000    35.000000    30.000000    30.000000    30.000000   
50%     165.000000   130.000000   125.000000   125.000000   140.000000   
75%     395.000000   370.000000   390.000000   395.000000   400.000000   
max    1855.000000  3665.000000  3130.000000  2720.000000  2155.000000   

         tot_40-45    tot_45-50    tot_50-55    tot_55-60    tot_60-65  \
count  4037.000000  4037.000000  4037.000000  4037.000000  4037.000000   
mean    277.389150   318.694575   317.168690   290.004954   261.013129   
std     296.310807   323.340649   313.494854   282.644514   252.283062   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%      45.000000    55.000000    60.000000    55.000000    50.000000   
50%     170.000000   205.000000   210.000000   195.000000   175.000000   
75%     440.000000   505.000000   500.000000   460.000000   420.000000   
max    2705.000000  2740.000000  2330.000000  1820.000000  1505.000000   

         tot_65-70    tot_70-75    tot_75-80    tot_80-85    tot_85-90  \
count  4037.000000  4037.000000  4037.000000  4037.000000  4037.000000   
mean    259.222195   180.671291   138.778796    97.865990    58.014615   
std     252.880706   180.394060   147.182601   110.731408    71.849267   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%      45.000000    30.000000    20.000000    10.000000     5.000000   
50%     170.000000   115.000000    85.000000    55.000000    25.000000   
75%     420.000000   290.000000   220.000000   155.000000    90.000000   
max    1515.000000  1050.000000   930.000000   825.000000   595.000000   

         tot_90-95      tot_95-       tot_man      man_0-5     man_5-10  \
count  4037.000000  4037.000000   4037.000000  4037.000000  4037.000000   
mean     24.066138     5.557345   2084.749814   111.306663   117.863513   
std      33.151787     9.066241   2069.832697   124.758421   129.580064   
min       0.000000     0.000000      0.000000     0.000000     0.000000   
25%       0.000000     0.000000    345.000000    15.000000    15.000000   
50%      10.000000     0.000000   1330.000000    60.000000    70.000000   
75%      35.000000    10.000000   3395.000000   175.000000   185.000000   
max     285.000000    95.000000  14145.000000  1115.000000  1205.000000   

         man_10-15    man_15-20   man_20-25    man_25-30    man_30-35  \
count  4037.000000  4037.000000  4037.00000  4037.000000  4037.000000   
mean    125.730741   129.199901   133.97944   133.957146   126.636116   
std     132.711762   131.823770   173.73238   172.877228   155.034259   
min       0.000000     0.000000     0.00000     0.000000     0.000000   
25%      20.000000    20.000000    20.00000    15.000000    15.000000   
50%      80.000000    85.000000    70.00000    65.000000    65.000000   
75%     195.000000   200.000000   195.00000   200.000000   195.000000   
max    1280.000000   950.000000  1735.00000  1470.000000  1315.000000   


In [7]:
#Convert all demographic data on number of inhabitants to fraction of total inhabitants in postal code
demo.iloc[:,2:67] = demo.iloc[:,2:67].div(demo.tot_inwoners, axis=0)
demo.head()

postcode  tot_inwoners   tot_0-5  tot_5-10  tot_10-15  tot_15-20  \
0      1011        9605.0  0.030713  0.030193   0.022905   0.032795   
1      1012        8245.0  0.026683  0.016374   0.013948   0.019406   
2      1013       21185.0  0.052396  0.040359   0.031862   0.032570   
3      1014         580.0  0.051724  0.025862   0.008621   0.025862   
4      1015       14860.0  0.038694  0.031292   0.028937   0.029946   

   tot_20-25  tot_25-30  tot_30-35  tot_35-40  tot_40-45  tot_45-50  \
0   0.092140   0.114524   0.086934   0.067673   0.064029   0.067673   
1   0.133414   0.206792   0.141298   0.084900   0.066101   0.061856   
2   0.060892   0.097947   0.101251   0.090158   0.078829   0.079537   
3   0.043103   0.232759   0.215517   0.103448   0.086207   0.060345   
4   0.073015   0.108008   0.097241   0.074361   0.072342   0.083109   

   tot_50-55  tot_55-60  tot_60-65  tot_65-70  tot_70-75  tot_75-80  \
0   0.080167   0.081728   0.078084   0.069755   0.037480   0.020822   
1   0.059430   0.050940   0.040631   0.036386   0.021831   0.010309   
2   0.076941   0.069389   0.063016   0.053576   0.031626   0.018881   
3   0.043103   0.043103   0.025862   0.017241   0.017241   0.017241   
4   0.079071   0.068977   0.062248   0.070996   0.038022   0.024226   

   tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man   man_0-5  man_5-10  \
0   0.011973   0.006247   0.003644  0.001562  0.519521  0.015096  0.014055   
1   0.004851   0.001819   0.000606  0.000000  0.545179  0.012735  0.007277   
2   0.012037   0.005664   0.002360  0.000708  0.501770  0.025490  0.021005   
3   0.008621   0.000000   0.000000  0.000000  0.577586  0.025862  0.008621   
4   0.012113   0.004711   0.002355  0.000336  0.506729  0.019179  0.015478   

   man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  man_35-40  \
0   0.010932   0.015617   0.038522   0.053618   0.045809   0.039563   
1   0.007277   0.007884   0.055791   0.102486   0.078229   0.053366   
2   0.016285   0.016757   0.027614   0.044843   0.050979   0.043899   
3   0.000000   0.017241   0.025862   0.129310   0.120690   0.060345   
4   0.014805   0.015141   0.030283   0.049125   0.048789   0.039704   

   man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  man_65-70  \
0   0.036960   0.040083   0.047892   0.044768   0.042686   0.036439   
1   0.043663   0.038205   0.040631   0.032747   0.023651   0.020619   
2   0.042011   0.043191   0.041539   0.034930   0.031626   0.027142   
3   0.060345   0.034483   0.034483   0.034483   0.017241   0.008621   
4   0.039031   0.045087   0.043742   0.037685   0.031629   0.036339   

   man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  tot_vrouw  \
0   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   0.480479   
1   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   0.454215   
2   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   0.498230   
3   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   0.422414   
4   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   0.493271   

   vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  vrouw_25-30  \
0   0.015617    0.015617     0.011973     0.016658     0.053618     0.060906   
1   0.014554    0.009096     0.007884     0.012129     0.078229     0.104912   
2   0.026906    0.019353     0.015577     0.015813     0.033278     0.053104   
3   0.034483    0.017241     0.000000     0.008621     0.025862     0.120690   
4   0.019515    0.015478     0.013795     0.015141     0.042732     0.058883   

   vrouw_30-35  vrouw_35-40  vrouw_40-45  vrouw_45-50  vrouw_50-55  \
0     0.041124     0.028110     0.027069     0.027590     0.032275   
1     0.063675     0.031534     0.022438     0.022438     0.019406   
2     0.050271     0.046259     0.036819     0.036346     0.035166   
3     0.094828     0.034483     0.025862     0.017241     0.008621   
4     0.048452     0.034657     0.033647     0.038022     0.034993   

   vrouw_5

In [8]:
#Convert all demographic data on number of households to fraction of total households in postal code
demo.iloc[:,68:71] = demo.iloc[:,68:71].div(demo.tot_huishoudens, axis=0)
demo.head()

postcode  tot_inwoners   tot_0-5  tot_5-10  tot_10-15  tot_15-20  \
0      1011        9605.0  0.030713  0.030193   0.022905   0.032795   
1      1012        8245.0  0.026683  0.016374   0.013948   0.019406   
2      1013       21185.0  0.052396  0.040359   0.031862   0.032570   
3      1014         580.0  0.051724  0.025862   0.008621   0.025862   
4      1015       14860.0  0.038694  0.031292   0.028937   0.029946   

   tot_20-25  tot_25-30  tot_30-35  tot_35-40  tot_40-45  tot_45-50  \
0   0.092140   0.114524   0.086934   0.067673   0.064029   0.067673   
1   0.133414   0.206792   0.141298   0.084900   0.066101   0.061856   
2   0.060892   0.097947   0.101251   0.090158   0.078829   0.079537   
3   0.043103   0.232759   0.215517   0.103448   0.086207   0.060345   
4   0.073015   0.108008   0.097241   0.074361   0.072342   0.083109   

   tot_50-55  tot_55-60  tot_60-65  tot_65-70  tot_70-75  tot_75-80  \
0   0.080167   0.081728   0.078084   0.069755   0.037480   0.020822   
1   0.059430   0.050940   0.040631   0.036386   0.021831   0.010309   
2   0.076941   0.069389   0.063016   0.053576   0.031626   0.018881   
3   0.043103   0.043103   0.025862   0.017241   0.017241   0.017241   
4   0.079071   0.068977   0.062248   0.070996   0.038022   0.024226   

   tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man   man_0-5  man_5-10  \
0   0.011973   0.006247   0.003644  0.001562  0.519521  0.015096  0.014055   
1   0.004851   0.001819   0.000606  0.000000  0.545179  0.012735  0.007277   
2   0.012037   0.005664   0.002360  0.000708  0.501770  0.025490  0.021005   
3   0.008621   0.000000   0.000000  0.000000  0.577586  0.025862  0.008621   
4   0.012113   0.004711   0.002355  0.000336  0.506729  0.019179  0.015478   

   man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  man_35-40  \
0   0.010932   0.015617   0.038522   0.053618   0.045809   0.039563   
1   0.007277   0.007884   0.055791   0.102486   0.078229   0.053366   
2   0.016285   0.016757   0.027614   0.044843   0.050979   0.043899   
3   0.000000   0.017241   0.025862   0.129310   0.120690   0.060345   
4   0.014805   0.015141   0.030283   0.049125   0.048789   0.039704   

   man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  man_65-70  \
0   0.036960   0.040083   0.047892   0.044768   0.042686   0.036439   
1   0.043663   0.038205   0.040631   0.032747   0.023651   0.020619   
2   0.042011   0.043191   0.041539   0.034930   0.031626   0.027142   
3   0.060345   0.034483   0.034483   0.034483   0.017241   0.008621   
4   0.039031   0.045087   0.043742   0.037685   0.031629   0.036339   

   man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  tot_vrouw  \
0   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   0.480479   
1   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   0.454215   
2   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   0.498230   
3   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   0.422414   
4   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   0.493271   

   vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  vrouw_25-30  \
0   0.015617    0.015617     0.011973     0.016658     0.053618     0.060906   
1   0.014554    0.009096     0.007884     0.012129     0.078229     0.104912   
2   0.026906    0.019353     0.015577     0.015813     0.033278     0.053104   
3   0.034483    0.017241     0.000000     0.008621     0.025862     0.120690   
4   0.019515    0.015478     0.013795     0.015141     0.042732     0.058883   

   vrouw_30-35  vrouw_35-40  vrouw_40-45  vrouw_45-50  vrouw_50-55  \
0     0.041124     0.028110     0.027069     0.027590     0.032275   
1     0.063675     0.031534     0.022438     0.022438     0.019406   
2     0.050271     0.046259     0.036819     0.036346     0.035166   
3     0.094828     0.034483     0.025862     0.017241     0.008621   
4     0.048452     0.034657     0.033647     0.038022     0.034993   

   vrouw_5

### Download geolocation data

This website offers datasets for geolocation per Dutch four digit postal codes.
https://git.tuxm.nl/tuxmachine/postcodes/src/4329c858db24b79523fd3fbbaf2df138ccaf16cd

Credit: https://git.tuxm.nl/tuxmachine/postcodes/src/master/README.md

License: https://git.tuxm.nl/tuxmachine/postcodes/src/master/LICENSE

In [9]:
#Four digit postal code LatLong in CSV dataset for Netherlands areas in LatLong geolocation
neighlatlong = pd.read_csv('https://git.tuxm.nl/tuxmachine/postcodes/raw/master/4pp.csv')
neighlatlong.head()

id  postcode woonplaats alternatieve_schrijfwijzen   gemeente  \
0   1      1000  Amsterdam                        NaN  Amsterdam   
1   2      1001  Amsterdam                        NaN  Amsterdam   
2   3      1002  Amsterdam                        NaN  Amsterdam   
3   4      1003  Amsterdam                        NaN  Amsterdam   
4   5      1005  Amsterdam                        NaN  Amsterdam   

       provincie  netnummer   latitude  longitude     soort  
0  Noord-Holland         20  52.336243   4.869444   Postbus  
1  Noord-Holland         20  52.364240   4.883358   Postbus  
2  Noord-Holland         20  52.364240   4.883358  Onbekend  
3  Noord-Holland         20  52.364240   4.883358  Onbekend  
4  Noord-Holland         20  52.364240   4.883358   Postbus

In [10]:
neighlatlong.shape

(4699, 10)

Drop all areas with category ('Soort') Postbus (=P.O. Box) or Onbekend (=Unkown)

In [11]:
#Drop all rows with Soort is Onbekend
neighlatlong.drop(neighlatlong[neighlatlong.soort == 'Onbekend'].index, inplace=True)
#Drop all rows with Soort is Postbus
neighlatlong.drop(neighlatlong[neighlatlong.soort == 'Postbus'].index, inplace=True)
neighlatlong.head()

id  postcode woonplaats alternatieve_schrijfwijzen   gemeente  \
9   10      1011  Amsterdam                        NaN  Amsterdam   
10  11      1012  Amsterdam                        NaN  Amsterdam   
11  12      1013  Amsterdam                        NaN  Amsterdam   
12  13      1014  Amsterdam                        NaN  Amsterdam   
13  14      1015  Amsterdam                        NaN  Amsterdam   

        provincie  netnummer   latitude  longitude  soort  
9   Noord-Holland         20  52.372976   4.903957  Adres  
10  Noord-Holland         20  52.373386   4.894064  Adres  
11  Noord-Holland         20  52.396789   4.876607  Adres  
12  Noord-Holland         20  52.392305   4.855884  Adres  
13  Noord-Holland         20  52.379093   4.885109  Adres

Drop all cities not being the cities we want to research: Amsterdam, Rotterdam, The Hague and Utrecht

In [12]:
# List of cities to select
cityselect = ['amsterdam','rotterdam','den haag','utrecht']
neighlatlong = neighlatlong[neighlatlong.woonplaats.str.contains('|'.join(cityselect), case=False)]
neighlatlong

id  postcode          woonplaats  alternatieve_schrijfwijzen  \
9       10      1011           Amsterdam                         NaN   
10      11      1012           Amsterdam                         NaN   
11      12      1013           Amsterdam                         NaN   
12      13      1014           Amsterdam                         NaN   
13      14      1015           Amsterdam                         NaN   
14      15      1016           Amsterdam                         NaN   
15      16      1017           Amsterdam                         NaN   
16      17      1018           Amsterdam                         NaN   
17      18      1019           Amsterdam                         NaN   
19      20      1021           Amsterdam                         NaN   
20      21      1022           Amsterdam                         NaN   
21      22      1023           Amsterdam                         NaN   
22      23      1024           Amsterdam                         NaN   
23      24      1025           Amsterdam                         NaN   
24      25      1026           Amsterdam                         NaN   
25      26      1027           Amsterdam                         NaN   
26      27      1028           Amsterdam                         NaN   
28      29      1031           Amsterdam                         NaN   
29      30      1032           Amsterdam                         NaN   
30      31      1033           Amsterdam                         NaN   
31      32      1034           Amsterdam                         NaN   
32      33      1035           Amsterdam                         NaN   
33      34      1036           Amsterdam                         NaN   
34      35      1037           Amsterdam                         NaN   
36      37      1041           Amsterdam                         NaN   
37      38      1042           Amsterdam                         NaN   
38      39      1043           Amsterdam                         NaN   
39      40      1044           Amsterdam                         NaN   
40      41      1045           Amsterdam                         NaN   
41      42      1046           Amsterdam                         NaN   
42      43      1047           Amsterdam                         NaN   
43      44      1051           Amsterdam                         NaN   
44      45      1052           Amsterdam                         NaN   
45      46      1053           Amsterdam                         NaN   
46      47      1054           Amsterdam                         NaN   
47      48      1055           Amsterdam                         NaN   
48      49      1056           Amsterdam                         NaN   
49      50      1057           Amsterdam                         NaN   
50      51      1058           Amsterdam                         NaN   
51      52      1059           Amsterdam                         NaN   
52      53      1060           Amsterdam                         NaN   
53      54      1061           Amsterdam                         NaN   
54      55      1062           Amsterdam                         NaN   
55      56      1063           Amsterdam                         NaN   
56      57      1064           Amsterdam                         NaN   
57      58      1065           Amsterdam                         NaN   
58      59      1066           Amsterdam                         NaN   
59      60      1067           Amsterdam                         NaN   
60      61      1068           Amsterdam                         NaN   
61      62      1069           Amsterdam                         NaN   
63      64      1071           Amsterdam                         NaN   
64      65      1072           Amsterdam                         NaN   
65      66      1073           Amsterdam                         NaN   
66      67      1074           Amsterdam                         NaN   
67      68      1075           Amsterdam        

In [13]:
#Oops, we have a city called Nieuw-Amsterdam completely somewhere else in the Netherlands. Drop that.
neighlatlong.drop(neighlatlong[neighlatlong.woonplaats == 'Nieuw-Amsterdam'].index, inplace=True)
neighlatlong

id  postcode          woonplaats  alternatieve_schrijfwijzen  \
9       10      1011           Amsterdam                         NaN   
10      11      1012           Amsterdam                         NaN   
11      12      1013           Amsterdam                         NaN   
12      13      1014           Amsterdam                         NaN   
13      14      1015           Amsterdam                         NaN   
14      15      1016           Amsterdam                         NaN   
15      16      1017           Amsterdam                         NaN   
16      17      1018           Amsterdam                         NaN   
17      18      1019           Amsterdam                         NaN   
19      20      1021           Amsterdam                         NaN   
20      21      1022           Amsterdam                         NaN   
21      22      1023           Amsterdam                         NaN   
22      23      1024           Amsterdam                         NaN   
23      24      1025           Amsterdam                         NaN   
24      25      1026           Amsterdam                         NaN   
25      26      1027           Amsterdam                         NaN   
26      27      1028           Amsterdam                         NaN   
28      29      1031           Amsterdam                         NaN   
29      30      1032           Amsterdam                         NaN   
30      31      1033           Amsterdam                         NaN   
31      32      1034           Amsterdam                         NaN   
32      33      1035           Amsterdam                         NaN   
33      34      1036           Amsterdam                         NaN   
34      35      1037           Amsterdam                         NaN   
36      37      1041           Amsterdam                         NaN   
37      38      1042           Amsterdam                         NaN   
38      39      1043           Amsterdam                         NaN   
39      40      1044           Amsterdam                         NaN   
40      41      1045           Amsterdam                         NaN   
41      42      1046           Amsterdam                         NaN   
42      43      1047           Amsterdam                         NaN   
43      44      1051           Amsterdam                         NaN   
44      45      1052           Amsterdam                         NaN   
45      46      1053           Amsterdam                         NaN   
46      47      1054           Amsterdam                         NaN   
47      48      1055           Amsterdam                         NaN   
48      49      1056           Amsterdam                         NaN   
49      50      1057           Amsterdam                         NaN   
50      51      1058           Amsterdam                         NaN   
51      52      1059           Amsterdam                         NaN   
52      53      1060           Amsterdam                         NaN   
53      54      1061           Amsterdam                         NaN   
54      55      1062           Amsterdam                         NaN   
55      56      1063           Amsterdam                         NaN   
56      57      1064           Amsterdam                         NaN   
57      58      1065           Amsterdam                         NaN   
58      59      1066           Amsterdam                         NaN   
59      60      1067           Amsterdam                         NaN   
60      61      1068           Amsterdam                         NaN   
61      62      1069           Amsterdam                         NaN   
63      64      1071           Amsterdam                         NaN   
64      65      1072           Amsterdam                         NaN   
65      66      1073           Amsterdam                         NaN   
66      67      1074           Amsterdam                         NaN   
67      68      1075           Amsterdam        

In [14]:
neighlatlong.shape

(252, 10)

In [15]:
neighlatlong.dtypes

id                              int64
postcode                        int64
woonplaats                     object
alternatieve_schrijfwijzen     object
gemeente                       object
provincie                      object
netnummer                       int64
latitude                      float64
longitude                     float64
soort                          object
dtype: object

In [16]:
neighlatlong.describe()

id     postcode   netnummer    latitude   longitude
count   252.000000   252.000000  252.000000  252.000000  252.000000
mean    715.353175  2367.206349   31.269841   52.131220    4.681036
std     491.045853   964.835282   22.879700    0.176728    0.306865
min      10.000000  1011.000000   10.000000   51.871742    4.218229
25%      77.750000  1086.750000   10.000000   51.965608    4.421880
50%     817.500000  2571.500000   20.000000   52.085449    4.665768
75%    1062.250000  3068.250000   30.000000   52.344597    4.937426
max    1356.000000  3585.000000   70.000000   52.423834    5.164979

### CBS income data per postal code

The Dutch Central Bureau of Statistics (CBS) has an open dataset on standardised income based on postal code.
See https://www.cbs.nl/nl-nl/maatwerk/2017/15/besteedbaar-inkomen-per-postcodegebied-2004-2014

In [17]:
#Excel has multi row header, so header is set to none. Only columns for latest year (2014) are imported.
#Columns are: postcode for first four digits postal code, gem_inkomen is average income, std_inkomen is standardised income corrected for householdsize
inkomen = pd.read_excel('https://www.cbs.nl/-/media/_excel/2017/15/besteedbaar-inkomen-postcode-2004-2014.xlsx',
                        sheet_name = 'Tabel1', header = None, usecols = [0, 23, 35], skiprows = 10, skipfooter = 5)
inkomen.columns = ['postcode', 'gem_inkomen', 'std_inkomen' ]
inkomen.head()

postcode gem_inkomen std_inkomen
0      1011          32        26.3
1      1012        26.2        22.4
2      1013        30.3        24.1
3      1014          35        28.5
4      1015        33.3        27.2

In [18]:
#Check data types
inkomen.dtypes

postcode        int64
gem_inkomen    object
std_inkomen    object
dtype: object

In [19]:
#Two income columns have converted to Object instead of Float due to fields containing - instead of zero. Correct this
inkomen['gem_inkomen'] = pd.to_numeric(inkomen['gem_inkomen'], errors='coerce')
inkomen['gem_inkomen'].fillna(0, inplace=True)
inkomen['std_inkomen'] = pd.to_numeric(inkomen['std_inkomen'], errors='coerce')
inkomen['std_inkomen'].fillna(0, inplace=True)
inkomen.head()

postcode  gem_inkomen  std_inkomen
0      1011         32.0         26.3
1      1012         26.2         22.4
2      1013         30.3         24.1
3      1014         35.0         28.5
4      1015         33.3         27.2

In [20]:
inkomen.shape

(4053, 3)

In [21]:
inkomen.dtypes

postcode         int64
gem_inkomen    float64
std_inkomen    float64
dtype: object

In [22]:
inkomen.describe()

postcode  gem_inkomen  std_inkomen
count  4053.000000  4053.000000  4053.000000
mean   5673.362941    32.684160    22.438959
std    2671.635711    14.333122     9.528407
min    1011.000000     0.000000     0.000000
25%    3331.000000    30.000000    21.800000
50%    5709.000000    36.400000    25.000000
75%    8045.000000    40.700000    27.200000
max    9999.000000   108.800000    76.800000

### CBS names of areas and neighbourhoods based on postal code

The Dutch Central Bureau of Statistics (CBS) has an open dataset on areas and neighbourhoods based on postal code.

See: https://www.cbs.nl/nl-nl/maatwerk/2018/36/buurt-wijk-en-gemeente-2018-voor-postcode-huisnummer

In [23]:
#Download and extract ZIP file of CBS area and neighbourhood data
!wget -q -O '2018-cbs-pc6huisnr20180801_buurt-vs2.zip' https://www.cbs.nl/-/media/_excel/2018/36/2018-cbs-pc6huisnr20180801_buurt%20-vs2.zip
with ZipFile('2018-cbs-pc6huisnr20180801_buurt-vs2.zip', 'r') as zipObj:
   # Extract all the contents of zip file in current directory
   zipObj.extractall()
print('Data downloaded!')

Data downloaded!


In [24]:
#Create dataframe on lowlevel postal code data
pc = pd.read_csv('pc6hnr20180801_gwb-vs2.csv', sep=';', encoding='latin_1')
pc.rename(columns = {'Buurt2018': 'buurtcode', 'Wijk2018': 'wijkcode', 'Gemeente2018': 'gemeentecode'}, inplace = True)
pc.head()

PC6  Huisnummer  buurtcode  wijkcode  gemeentecode
0  1011AB         105    3630400     36304           363
1  1011AB         106    3630400     36304           363
2  1011AB         107    3630400     36304           363
3  1011AB         110    3630400     36304           363
4  1011AB         112    3630400     36304           363

In [25]:
#Create dataframe with neighbourhood codes and names
wijk = pd.read_csv('wijknaam2018.csv', sep=';', encoding='latin_1')
wijk.rename(columns = {'GWBcode8': 'wijkcode', 'GWBlabel': 'wijk'}, inplace = True)
wijk.head()

wijkcode          wijk
0       300       Wijk 00
1       500       Wijk 00
2       900  Wijk 00 West
3       901  Wijk 01 Oost
4      1000  Wijk 00 Stad

In [26]:
#Create dataframe with area codes and names
buurt = pd.read_csv('buurtnaam2018.csv', sep=';', encoding='latin_1')
buurt.rename(columns = {'GWBcode8': 'buurtcode', 'GWBlabel': 'buurt'}, inplace = True)
buurt.head()

buurtcode                                        buurt
0      30000                           Appingedam-Centrum
1      30001                              Appingedam-West
2      30002                              Appingedam-Oost
3      30007  Verspreide huizen Damsterdiep en Eemskanaal
4      30008  Verspreide huizen ten zuiden van Eemskanaal

In [27]:
#Merge postal code dataframe with neighbourhood and area names
pcmerge = pd.merge(pc, wijk, on='wijkcode')
pcmerge = pd.merge(pcmerge, buurt, on='buurtcode')
pcmerge.head()

PC6  Huisnummer  buurtcode  wijkcode  gemeentecode                wijk  \
0  1011AB         105    3630400     36304           363  Nieuwmarkt/Lastage   
1  1011AB         106    3630400     36304           363  Nieuwmarkt/Lastage   
2  1011AB         107    3630400     36304           363  Nieuwmarkt/Lastage   
3  1011AB         110    3630400     36304           363  Nieuwmarkt/Lastage   
4  1011AB         112    3630400     36304           363  Nieuwmarkt/Lastage   

              buurt  
0  Oosterdokseiland  
1  Oosterdokseiland  
2  Oosterdokseiland  
3  Oosterdokseiland  
4  Oosterdokseiland

In [28]:
#Drop columns we will not need: housenumber (too low level), Municipality (will be added by geocode data by name instead of code) and the codes
pcmerge.drop(['Huisnummer', 'buurtcode', 'wijkcode', 'gemeentecode'], axis=1, inplace = True)
pcmerge.head()

PC6                wijk             buurt
0  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland
1  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland
2  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland
3  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland
4  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland

In [29]:
#Create column with first four digits of postal code as all six is too low level
pcmerge['postcode'] = pcmerge['PC6'].str[:4]
pcmerge.head()

PC6                wijk             buurt postcode
0  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland     1011
1  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland     1011
2  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland     1011
3  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland     1011
4  1011AB  Nieuwmarkt/Lastage  Oosterdokseiland     1011

In [30]:
#Drop PC6 and group on postcode
postcode = pcmerge.groupby(['postcode'], as_index=False).first()
postcode.drop(['PC6'], axis=1, inplace = True)
postcode.head()

postcode                     wijk               buurt
0     1011       Nieuwmarkt/Lastage    Oosterdokseiland
1     1012  Burgwallen-Nieuwe Zijde  Stationsplein e.o.
2     1013          Haarlemmerbuurt    Westerdokseiland
3     1014    Westelijk Havengebied       Alfa-driehoek
4     1015      Grachtengordel-West    Langestraat e.o.

In [31]:
postcode.dtypes

postcode    object
wijk        object
buurt       object
dtype: object

In [32]:
#Cast column postcode to INT instead of OBJECT
postcode.postcode = postcode.postcode.astype('int64')
postcode.dtypes

postcode     int64
wijk        object
buurt       object
dtype: object

In [33]:
#Now merge with long/lat
postcode = pd.merge(postcode, neighlatlong, on='postcode')
postcode.head()

postcode                     wijk               buurt  id woonplaats  \
0      1011       Nieuwmarkt/Lastage    Oosterdokseiland  10  Amsterdam   
1      1012  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  11  Amsterdam   
2      1013          Haarlemmerbuurt    Westerdokseiland  12  Amsterdam   
3      1014    Westelijk Havengebied       Alfa-driehoek  13  Amsterdam   
4      1015      Grachtengordel-West    Langestraat e.o.  14  Amsterdam   

  alternatieve_schrijfwijzen   gemeente      provincie  netnummer   latitude  \
0                        NaN  Amsterdam  Noord-Holland         20  52.372976   
1                        NaN  Amsterdam  Noord-Holland         20  52.373386   
2                        NaN  Amsterdam  Noord-Holland         20  52.396789   
3                        NaN  Amsterdam  Noord-Holland         20  52.392305   
4                        NaN  Amsterdam  Noord-Holland         20  52.379093   

   longitude  soort  
0   4.903957  Adres  
1   4.894064  Adres  
2   4.876607  Adres  
3   4.855884  Adres  
4   4.885109  Adres

In [34]:
#Now merge with demographic data
postcode = pd.merge(postcode, demo, on='postcode')
postcode.head()

postcode                     wijk               buurt  id woonplaats  \
0      1011       Nieuwmarkt/Lastage    Oosterdokseiland  10  Amsterdam   
1      1012  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  11  Amsterdam   
2      1013          Haarlemmerbuurt    Westerdokseiland  12  Amsterdam   
3      1014    Westelijk Havengebied       Alfa-driehoek  13  Amsterdam   
4      1015      Grachtengordel-West    Langestraat e.o.  14  Amsterdam   

  alternatieve_schrijfwijzen   gemeente      provincie  netnummer   latitude  \
0                        NaN  Amsterdam  Noord-Holland         20  52.372976   
1                        NaN  Amsterdam  Noord-Holland         20  52.373386   
2                        NaN  Amsterdam  Noord-Holland         20  52.396789   
3                        NaN  Amsterdam  Noord-Holland         20  52.392305   
4                        NaN  Amsterdam  Noord-Holland         20  52.379093   

   longitude  soort  tot_inwoners   tot_0-5  tot_5-10  tot_10-15  tot_15-20  \
0   4.903957  Adres        9605.0  0.030713  0.030193   0.022905   0.032795   
1   4.894064  Adres        8245.0  0.026683  0.016374   0.013948   0.019406   
2   4.876607  Adres       21185.0  0.052396  0.040359   0.031862   0.032570   
3   4.855884  Adres         580.0  0.051724  0.025862   0.008621   0.025862   
4   4.885109  Adres       14860.0  0.038694  0.031292   0.028937   0.029946   

   tot_20-25  tot_25-30  tot_30-35  tot_35-40  tot_40-45  tot_45-50  \
0   0.092140   0.114524   0.086934   0.067673   0.064029   0.067673   
1   0.133414   0.206792   0.141298   0.084900   0.066101   0.061856   
2   0.060892   0.097947   0.101251   0.090158   0.078829   0.079537   
3   0.043103   0.232759   0.215517   0.103448   0.086207   0.060345   
4   0.073015   0.108008   0.097241   0.074361   0.072342   0.083109   

   tot_50-55  tot_55-60  tot_60-65  tot_65-70  tot_70-75  tot_75-80  \
0   0.080167   0.081728   0.078084   0.069755   0.037480   0.020822   
1   0.059430   0.050940   0.040631   0.036386   0.021831   0.010309   
2   0.076941   0.069389   0.063016   0.053576   0.031626   0.018881   
3   0.043103   0.043103   0.025862   0.017241   0.017241   0.017241   
4   0.079071   0.068977   0.062248   0.070996   0.038022   0.024226   

   tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man   man_0-5  man_5-10  \
0   0.011973   0.006247   0.003644  0.001562  0.519521  0.015096  0.014055   
1   0.004851   0.001819   0.000606  0.000000  0.545179  0.012735  0.007277   
2   0.012037   0.005664   0.002360  0.000708  0.501770  0.025490  0.021005   
3   0.008621   0.000000   0.000000  0.000000  0.577586  0.025862  0.008621   
4   0.012113   0.004711   0.002355  0.000336  0.506729  0.019179  0.015478   

   man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  man_35-40  \
0   0.010932   0.015617   0.038522   0.053618   0.045809   0.039563   
1   0.007277   0.007884   0.055791   0.102486   0.078229   0.053366   
2   0.016285   0.016757   0.027614   0.044843   0.050979   0.043899   
3   0.000000   0.017241   0.025862   0.129310   0.120690   0.060345   
4   0.014805   0.015141   0.030283   0.049125   0.048789   0.039704   

   man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  man_65-70  \
0   0.036960   0.040083   0.047892   0.044768   0.042686   0.036439   
1   0.043663   0.038205   0.040631   0.032747   0.023651   0.020619   
2   0.042011   0.043191   0.041539   0.034930   0.031626   0.027142   
3   0.060345   0.034483   0.034483   0.034483   0.017241   0.008621   
4   0.039031   0.045087   0.043742   0.037685   0.031629   0.036339   

   man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  tot_vrouw  \
0   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   0.480479   
1   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   0.454215   
2   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   0.498230   
3   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   0.422414   
4   0.019852  

In [35]:
#Drop unneeded columns
postcode.drop(['id', 'alternatieve_schrijfwijzen', 'netnummer', 'soort'], axis=1, inplace = True)
postcode.head()

postcode                     wijk               buurt woonplaats  \
0      1011       Nieuwmarkt/Lastage    Oosterdokseiland  Amsterdam   
1      1012  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  Amsterdam   
2      1013          Haarlemmerbuurt    Westerdokseiland  Amsterdam   
3      1014    Westelijk Havengebied       Alfa-driehoek  Amsterdam   
4      1015      Grachtengordel-West    Langestraat e.o.  Amsterdam   

    gemeente      provincie   latitude  longitude  tot_inwoners   tot_0-5  \
0  Amsterdam  Noord-Holland  52.372976   4.903957        9605.0  0.030713   
1  Amsterdam  Noord-Holland  52.373386   4.894064        8245.0  0.026683   
2  Amsterdam  Noord-Holland  52.396789   4.876607       21185.0  0.052396   
3  Amsterdam  Noord-Holland  52.392305   4.855884         580.0  0.051724   
4  Amsterdam  Noord-Holland  52.379093   4.885109       14860.0  0.038694   

   tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  tot_35-40  \
0  0.030193   0.022905   0.032795   0.092140   0.114524   0.086934   0.067673   
1  0.016374   0.013948   0.019406   0.133414   0.206792   0.141298   0.084900   
2  0.040359   0.031862   0.032570   0.060892   0.097947   0.101251   0.090158   
3  0.025862   0.008621   0.025862   0.043103   0.232759   0.215517   0.103448   
4  0.031292   0.028937   0.029946   0.073015   0.108008   0.097241   0.074361   

   tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  tot_65-70  \
0   0.064029   0.067673   0.080167   0.081728   0.078084   0.069755   
1   0.066101   0.061856   0.059430   0.050940   0.040631   0.036386   
2   0.078829   0.079537   0.076941   0.069389   0.063016   0.053576   
3   0.086207   0.060345   0.043103   0.043103   0.025862   0.017241   
4   0.072342   0.083109   0.079071   0.068977   0.062248   0.070996   

   tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man  \
0   0.037480   0.020822   0.011973   0.006247   0.003644  0.001562  0.519521   
1   0.021831   0.010309   0.004851   0.001819   0.000606  0.000000  0.545179   
2   0.031626   0.018881   0.012037   0.005664   0.002360  0.000708  0.501770   
3   0.017241   0.017241   0.008621   0.000000   0.000000  0.000000  0.577586   
4   0.038022   0.024226   0.012113   0.004711   0.002355  0.000336  0.506729   

    man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  \
0  0.015096  0.014055   0.010932   0.015617   0.038522   0.053618   0.045809   
1  0.012735  0.007277   0.007277   0.007884   0.055791   0.102486   0.078229   
2  0.025490  0.021005   0.016285   0.016757   0.027614   0.044843   0.050979   
3  0.025862  0.008621   0.000000   0.017241   0.025862   0.129310   0.120690   
4  0.019179  0.015478   0.014805   0.015141   0.030283   0.049125   0.048789   

   man_35-40  man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  \
0   0.039563   0.036960   0.040083   0.047892   0.044768   0.042686   
1   0.053366   0.043663   0.038205   0.040631   0.032747   0.023651   
2   0.043899   0.042011   0.043191   0.041539   0.034930   0.031626   
3   0.060345   0.060345   0.034483   0.034483   0.034483   0.017241   
4   0.039704   0.039031   0.045087   0.043742   0.037685   0.031629   

   man_65-70  man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  \
0   0.036439   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   
1   0.020619   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   
2   0.027142   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   
3   0.008621   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   
4   0.036339   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   

   tot_vrouw  vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  \
0   0.480479   0.015617    0.015617     0.011973     0.016658     0.053618   
1   0.454215   0.014554    0.009096     0.007884     0.012129     0.078229   
2   0.498230   0.026906    0.019353     0.015577     0.015813     0.033278   
3   0.42241

In [36]:
#Now merge with income data
postcode = pd.merge(postcode, inkomen, on='postcode')
postcode.head()

postcode                     wijk               buurt woonplaats  \
0      1011       Nieuwmarkt/Lastage    Oosterdokseiland  Amsterdam   
1      1012  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  Amsterdam   
2      1013          Haarlemmerbuurt    Westerdokseiland  Amsterdam   
3      1014    Westelijk Havengebied       Alfa-driehoek  Amsterdam   
4      1015      Grachtengordel-West    Langestraat e.o.  Amsterdam   

    gemeente      provincie   latitude  longitude  tot_inwoners   tot_0-5  \
0  Amsterdam  Noord-Holland  52.372976   4.903957        9605.0  0.030713   
1  Amsterdam  Noord-Holland  52.373386   4.894064        8245.0  0.026683   
2  Amsterdam  Noord-Holland  52.396789   4.876607       21185.0  0.052396   
3  Amsterdam  Noord-Holland  52.392305   4.855884         580.0  0.051724   
4  Amsterdam  Noord-Holland  52.379093   4.885109       14860.0  0.038694   

   tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  tot_35-40  \
0  0.030193   0.022905   0.032795   0.092140   0.114524   0.086934   0.067673   
1  0.016374   0.013948   0.019406   0.133414   0.206792   0.141298   0.084900   
2  0.040359   0.031862   0.032570   0.060892   0.097947   0.101251   0.090158   
3  0.025862   0.008621   0.025862   0.043103   0.232759   0.215517   0.103448   
4  0.031292   0.028937   0.029946   0.073015   0.108008   0.097241   0.074361   

   tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  tot_65-70  \
0   0.064029   0.067673   0.080167   0.081728   0.078084   0.069755   
1   0.066101   0.061856   0.059430   0.050940   0.040631   0.036386   
2   0.078829   0.079537   0.076941   0.069389   0.063016   0.053576   
3   0.086207   0.060345   0.043103   0.043103   0.025862   0.017241   
4   0.072342   0.083109   0.079071   0.068977   0.062248   0.070996   

   tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man  \
0   0.037480   0.020822   0.011973   0.006247   0.003644  0.001562  0.519521   
1   0.021831   0.010309   0.004851   0.001819   0.000606  0.000000  0.545179   
2   0.031626   0.018881   0.012037   0.005664   0.002360  0.000708  0.501770   
3   0.017241   0.017241   0.008621   0.000000   0.000000  0.000000  0.577586   
4   0.038022   0.024226   0.012113   0.004711   0.002355  0.000336  0.506729   

    man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  \
0  0.015096  0.014055   0.010932   0.015617   0.038522   0.053618   0.045809   
1  0.012735  0.007277   0.007277   0.007884   0.055791   0.102486   0.078229   
2  0.025490  0.021005   0.016285   0.016757   0.027614   0.044843   0.050979   
3  0.025862  0.008621   0.000000   0.017241   0.025862   0.129310   0.120690   
4  0.019179  0.015478   0.014805   0.015141   0.030283   0.049125   0.048789   

   man_35-40  man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  \
0   0.039563   0.036960   0.040083   0.047892   0.044768   0.042686   
1   0.053366   0.043663   0.038205   0.040631   0.032747   0.023651   
2   0.043899   0.042011   0.043191   0.041539   0.034930   0.031626   
3   0.060345   0.060345   0.034483   0.034483   0.034483   0.017241   
4   0.039704   0.039031   0.045087   0.043742   0.037685   0.031629   

   man_65-70  man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  \
0   0.036439   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   
1   0.020619   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   
2   0.027142   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   
3   0.008621   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   
4   0.036339   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   

   tot_vrouw  vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  \
0   0.480479   0.015617    0.015617     0.011973     0.016658     0.053618   
1   0.454215   0.014554    0.009096     0.007884     0.012129     0.078229   
2   0.498230   0.026906    0.019353     0.015577     0.015813     0.033278   
3   0.42241

In [37]:
postcode.shape

(248, 81)

In [38]:
postcode.dtypes

postcode                    int64
wijk                       object
buurt                      object
woonplaats                 object
gemeente                   object
provincie                  object
latitude                  float64
longitude                 float64
tot_inwoners              float64
tot_0-5                   float64
tot_5-10                  float64
tot_10-15                 float64
tot_15-20                 float64
tot_20-25                 float64
tot_25-30                 float64
tot_30-35                 float64
tot_35-40                 float64
tot_40-45                 float64
tot_45-50                 float64
tot_50-55                 float64
tot_55-60                 float64
tot_60-65                 float64
tot_65-70                 float64
tot_70-75                 float64
tot_75-80                 float64
tot_80-85                 float64
tot_85-90                 float64
tot_90-95                 float64
tot_95-                   float64
tot_man       

In [39]:
# Obtain latitude and longitude of the Netherlands
g = geocoder.arcgis('Alphen aan de Rijn, Netherlands') # Choice for Woerden as it centers on the Randstad area where our four selected cities are
NL_coords = g.latlng
NL_coords

[52.12743000000006, 4.658820000000048]

### Test map of all postcal codes selected on the map of the Netherlands

In [40]:
#Startpoint of map
nl_map = folium.Map(location=[NL_coords[0], NL_coords[1]], zoom_start=9)

#Add area markers for each postal code in file
for lat, lng, pc4 in zip(postcode['latitude'], postcode['longitude'], postcode['postcode']):
    label = pc4
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(nl_map)  

# display map
nl_map

In [41]:
# Obtain latitude and longitude of the Netherlands
g = geocoder.arcgis('Utrecht, Netherlands')
Utrecht_coords = g.latlng
print("Utrecht", Utrecht_coords)
g = geocoder.arcgis('Amsterdam, Netherlands')
amsterdam_coords = g.latlng
print("Amsterdam", amsterdam_coords)
g = geocoder.arcgis('Rotterdam, Netherlands')
rotterdam_coords = g.latlng
print("Rotterdam", rotterdam_coords)
g = geocoder.arcgis('Den Haag, Netherlands')
denhaag_coords = g.latlng
print("The Hague", denhaag_coords)

Utrecht [52.08965000000006, 5.114350000000059]
Amsterdam [52.36993000000007, 4.907880000000034]
Rotterdam [51.92282000000006, 4.478480000000047]
The Hague [52.08409000000006, 4.317320000000052]


### Obtain Foursquare data on venues near to postal code center point

Hidden cell below containing secret Foursquare credentials.

In [42]:
# The code was removed by Watson Studio for sharing.

In [43]:
# Funtion to explore neighbourhood in Foursquare

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['postcode', 
                  'latitude', 
                  'longitude', 
                  'venue', 
                  'venue latitude', 
                  'venue longitude', 
                  'venue category']
    
    return(nearby_venues)

In [46]:
venues = getNearbyVenues(names=postcode['postcode'],
                         latitudes=postcode['latitude'],
                         longitudes=postcode['longitude']
                         )

1011
1012
1013
1014
1015
1016
1017
1018
1019
1021
1022
1023
1024
1025
1026
1027
1028
1031
1032
1033
1034
1035
1036
1037
1041
1042
1043
1045
1046
1047
1051
1052
1053
1054
1055
1056
1057
1058
1059
1060
1061
1062
1063
1064
1065
1066
1067
1068
1069
1071
1072
1073
1074
1075
1076
1077
1078
1079
1081
1082
1083
1086
1087
1091
1092
1093
1094
1095
1096
1097
1098
1101
1102
1103
1104
1105
1106
1107
1108
1109
2491
2492
2493
2495
2496
2497
2498
2511
2512
2513
2514
2515
2516
2517
2518
2521
2522
2523
2524
2525
2526
2531
2532
2533
2541
2542
2543
2544
2545
2546
2547
2548
2551
2552
2553
2554
2555
2561
2562
2563
2564
2565
2566
2571
2572
2573
2574
2581
2582
2583
2584
2585
2586
2587
2591
2592
2593
2594
2595
2596
2597
3011
3012
3013
3014
3015
3016
3021
3022
3023
3024
3025
3026
3027
3028
3029
3031
3032
3033
3034
3035
3036
3037
3038
3039
3041
3042
3043
3044
3045
3046
3047
3051
3052
3053
3054
3055
3056
3059
3061
3062
3063
3064
3065
3066
3067
3068
3069
3071
3072
3073
3074
3075
3076
3077
3078
3079
3081
3082
3083


In [47]:
# Explore result
print(venues.shape)
venues.head()

(5260, 7)


postcode   latitude  longitude                 venue  venue latitude  \
0      1011  52.372976   4.903957                  OCHA       52.374024   
1      1011  52.372976   4.903957            Black Gold       52.371787   
2      1011  52.372976   4.903957  The Hendrick's Hotel       52.373597   
3      1011  52.372976   4.903957          Eetcafé Bern       52.372575   
4      1011  52.372976   4.903957                   HPS       52.371683   

   venue longitude    venue category  
0         4.901683   Thai Restaurant  
1         4.903056       Record Shop  
2         4.906002             Hotel  
3         4.900645  Swiss Restaurant  
4         4.907673      Cocktail Bar

In [48]:
#Explore number per postal code
venues.groupby('postcode').count()

latitude  longitude  venue  venue latitude  venue longitude  \
postcode                                                                
1011           100        100    100             100              100   
1012           100        100    100             100              100   
1013             7          7      7               7                7   
1014            13         13     13              13               13   
1015           100        100    100             100              100   
1016           100        100    100             100              100   
1017           100        100    100             100              100   
1018            48         48     48              48               48   
1019            28         28     28              28               28   
1021            15         15     15              15               15   
1022            20         20     20              20               20   
1023             7          7      7               7                7   
1024             5          5      5               5                5   
1025            27         27     27              27               27   
1026             3          3      3               3                3   
1027             3          3      3               3                3   
1031             9          9      9               9                9   
1032            18         18     18              18               18   
1033             5          5      5               5                5   
1034            10         10     10              10               10   
1035             8          8      8               8                8   
1036             5          5      5               5                5   
1037             2          2      2               2                2   
1041             2          2      2               2                2   
1042             1          1      1               1                1   
1043             4          4      4               4                4   
1046             4          4      4               4                4   
1047             4          4      4               4                4   
1051            33         33     33              33               33   
1052            56         56     56              56               56   
1053           100        100    100             100              100   
1054            56         56     56              56               56   
1055            33         33     33              33               33   
1056            45         45     45              45               45   
1057            55         55     55              55               55   
1058            22         22     22              22               22   
1059            17         17     17              17               17   
1060             9          9      9               9                9   
1061             9          9      9               9                9   
1062            23         23     23              23               23   
1063            28         28     28              28               28   
1064            11         11     11              11               11   
1065            16         16     16              16               16   
1066             5          5      5               5                5   
1067             4          4      4               4                4   
1068            32         32     32              32               32   
1069            10         10     10              10               10   
1071            55         55     55              55               55   
1072           100        100    100             100              100   
1073            99         99     99              99               99   
1074            58         58     58              58               58   
1075            34         34     34              34               34   
1076            41         41     41              41               4

In [49]:
#Explore unique categories
print('There are {} uniques categories.'.format(len(venues['venue category'].unique())))

There are 351 uniques categories.


In [50]:
# one hot encoding
venue_onehot = pd.get_dummies(venues[['venue category']], prefix="", prefix_sep="")

# add postcode column back to dataframe
venue_onehot['postcode'] = venues['postcode']

#Explore
print(venue_onehot.shape)
venue_onehot.head()

(5260, 352)


Accessories Store  Advertising Agency  Afghan Restaurant  \
0                  0                   0                  0   
1                  0                   0                  0   
2                  0                   0                  0   
3                  0                   0                  0   
4                  0                   0                  0   

   African Restaurant  American Restaurant  Aquarium  Arcade  \
0                   0                    0         0       0   
1                   0                    0         0       0   
2                   0                    0         0       0   
3                   0                    0         0       0   
4                   0                    0         0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Assisted Living  \
0                     0                 0                0   
1                     0                 0                0   
2                     0                 0                0   
3                     0                 0                0   
4                     0                 0                0   

   Athletics & Sports  Australian Restaurant  Auto Dealership  Auto Garage  \
0                   0                      0                0            0   
1                   0                      0                0            0   
2                   0                      0                0            0   
3                   0                      0                0            0   
4                   0                      0                0            0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bar  Baseball Field  \
0          0           0           0       0    0               0   
1          0           0           0       0    0               0   
2          0           0           0       0    0               0   
3          0           0           0       0    0               0   
4          0           0           0       0    0               0   

   Basketball Court  Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  \
0                 0      0          0                0         0            0   
1                 0      0          0                0         0            0   
2                 0      0          0                0         0            0   
3                 0      0          0                0         0            0   
4                 0      0          0                0         0            0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Bistro  \
0           0              0                         0          0       0   
1           0              0                         0          0       0   
2           0              0                         0          0       0   
3           0              0                         0          0       0   
4           0              0                         0          0       0   

   Board Shop  Boarding House  Boat or Ferry  Bookstore  Bougatsa Shop  \
0           0               0              0          0              0   
1           0               0              0          0              0   
2           0               0              0          0              0   
3           0               0              0          0              0   
4           0               0              0          0              0   

   Boutique  Bowling Alley  Brasserie  Brazilian Restaurant  Breakfast Spot  \
0         0              0          0                    

In [51]:
#Group rows by neighborhood and take the mean of the frequency of occurrence of each category
venue_grouped = venue_onehot.groupby('postcode').mean().reset_index()
venue_grouped

postcode  Accessories Store  Advertising Agency  Afghan Restaurant  \
0        1011               0.00            0.000000           0.000000   
1        1012               0.00            0.000000           0.000000   
2        1013               0.00            0.142857           0.000000   
3        1014               0.00            0.000000           0.000000   
4        1015               0.00            0.000000           0.000000   
5        1016               0.00            0.000000           0.000000   
6        1017               0.00            0.000000           0.000000   
7        1018               0.00            0.000000           0.000000   
8        1019               0.00            0.000000           0.000000   
9        1021               0.00            0.000000           0.000000   
10       1022               0.00            0.000000           0.000000   
11       1023               0.00            0.000000           0.000000   
12       1024               0.00            0.000000           0.000000   
13       1025               0.00            0.000000           0.000000   
14       1026               0.00            0.000000           0.000000   
15       1027               0.00            0.000000           0.000000   
16       1031               0.00            0.000000           0.000000   
17       1032               0.00            0.000000           0.000000   
18       1033               0.00            0.000000           0.000000   
19       1034               0.00            0.000000           0.000000   
20       1035               0.00            0.000000           0.000000   
21       1036               0.00            0.000000           0.000000   
22       1037               0.00            0.000000           0.000000   
23       1041               0.00            0.000000           0.000000   
24       1042               0.00            0.000000           0.000000   
25       1043               0.00            0.000000           0.000000   
26       1046               0.00            0.000000           0.000000   
27       1047               0.00            0.000000           0.000000   
28       1051               0.00            0.000000           0.000000   
29       1052               0.00            0.000000           0.017857   
30       1053               0.00            0.000000           0.000000   
31       1054               0.00            0.000000           0.000000   
32       1055               0.00            0.000000           0.000000   
33       1056               0.00            0.000000           0.000000   
34       1057               0.00            0.000000           0.000000   
35       1058               0.00            0.000000           0.000000   
36       1059               0.00            0.000000           0.000000   
37       1060               0.00            0.000000           0.000000   
38       1061               0.00            0.000000           0.000000   
39       1062               0.00            0.000000           0.000000   
40       1063               0.00            0.000000           0.000000   
41       1064               0.00            0.000000           0.000000   
42       1065               0.00            0.000000           0.000000   
43       1066               0.00            0.000000           0.000000   
44       1067               0.00            0.000000           0.000000   
45       1068               0.00            0.000000           0.000000   
46       1069               0.00            0.000000           0.000000   
47       1071               0.00            0.000000           0.000000   
48       1072               0.01            0.000000           0.000000   
49       1073               0.00            0.000000           0.000000   
50       1074               0.00            0.000000           0.000000   
51       1075               0.00            0.000000           0.000000   
52       1076               0.

In [52]:
#Explore size
venue_grouped.shape

(244, 352)

In [53]:
#Function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [54]:
#Create new dataframe and display the top 10 venues for each neighborhood.

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['postcode']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
venue_sorted = pd.DataFrame(columns=columns)
venue_sorted['postcode'] = venue_grouped['postcode']

for ind in np.arange(venue_grouped.shape[0]):
    venue_sorted.iloc[ind, 1:] = return_most_common_venues(venue_grouped.iloc[ind, :], num_top_venues)

venue_sorted

postcode          1st Most Common Venue      2nd Most Common Venue  \
0        1011                            Bar                      Hotel   
1        1012                            Bar                Coffee Shop   
2        1013                         Office                    Theater   
3        1014                    Music Venue               Soccer Field   
4        1015                            Bar         Italian Restaurant   
5        1016                          Hotel                        Bar   
6        1017             Italian Restaurant                      Hotel   
7        1018                    Zoo Exhibit                 Restaurant   
8        1019                    Snack Place                Supermarket   
9        1021                        Brewery             Gymnastics Gym   
10       1022                           Park                   Bus Stop   
11       1023                Harbor / Marina                   Bus Stop   
12       1024                 Discount Store                   Bus Stop   
13       1025                    Supermarket           Department Store   
14       1026                Harbor / Marina             Boarding House   
15       1027                           Farm                 Campground   
16       1031                           Park                        Bar   
17       1032                           Café                       Park   
18       1033         Furniture / Home Store           Department Store   
19       1034                       Bus Stop                     Church   
20       1035                         Office       Gym / Fitness Center   
21       1036                       Bus Stop            Harbor / Marina   
22       1037                   Intersection                       Lake   
23       1041                Harbor / Marina                      Canal   
24       1042                Harbor / Marina                Zoo Exhibit   
25       1043                    Music Venue                     Garden   
26       1046                    Snack Place             Sandwich Place   
27       1047                    Coffee Shop                Music Venue   
28       1051                 Farmers Market                   Bus Stop   
29       1052                            Bar                Coffee Shop   
30       1053                           Café                        Bar   
31       1054           Ethiopian Restaurant                        Bar   
32       1055                            Bar               Tram Station   
33       1056                            Bar  Middle Eastern Restaurant   
34       1057                     Restaurant               Tram Station   
35       1058                            Bar                 Restaurant   
36       1059                     Restaurant                      Hotel   
37       1060                Bed & Breakfast                     Bakery   
38       1061                     Restaurant         Athletics & Sports   
39       1062                    Coffee Shop                Supermarket   
40       1063             Turkish Restaurant               Dessert Shop   
41       1064                           Park                 Playground   
42       1065               Asian Restaurant         Italian Restaurant   
43       1066         Furniture / Home Store                    Stables   
44       1067                   Soccer Field                    Stadium   
45       1068                 Clothing Store                Supermarket   
46       1069          Indonesian Restaurant          Convenience Store   
47       1071                          Hotel          French Restaurant   
48       1072                    Pizza Place                     Bakery   
49       1073                    Pizza Place         Italian Restaurant   
50       1074                            Bar         Italian Restaurant   
51       1075                            Bar      Indonesian Restaurant   
52       1076                 

In [55]:
venue_sorted.shape

(244, 11)

### Cluster postal code areas based on venue type, demographic data and income data

Prepare dataset to cluster on

In [56]:
#Merge postcode income data with data on mean frequency of venue category
clustering = pd.merge(postcode,venue_grouped, on='postcode')

#Drop location names and geographic data
clustering = postcode.iloc[:, 8:]

#Normalize dataset
clustering = StandardScaler().fit_transform(clustering)

clustering

array([[ 0.1251347 , -1.17933201, -0.95526156, ..., -1.22549638,
         0.19135092,  0.51067319],
       [-0.12585654, -1.35680384, -1.60641964, ..., -1.60797463,
        -0.27365864,  0.05881782],
       [ 2.26225128, -0.22456853, -0.47622988, ..., -0.78417532,
         0.05505501,  0.25578042],
       ...,
       [-0.51710759,  0.05636636,  0.12231514, ..., -0.19574724,
         0.9449871 ,  0.88142632],
       [-0.31963654, -1.98094908, -1.59206259, ..., -2.01987429,
        -0.87496411, -0.85647897],
       [-1.61427149, -0.08542127,  1.54874682, ...,  0.8928447 ,
        -2.37421907, -2.53645408]])

Perform k-Means clustering

In [57]:
# set number of clusters
kclusters = 5

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([3, 3, 3, 3, 3, 3, 3, 3, 2, 2, 2, 1, 2, 1, 1, 1, 1, 2, 1, 1, 2, 1,
       2, 1, 0, 0, 0, 0, 0, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 2, 3, 2, 2,
       2, 2, 2, 1, 2, 1, 3, 3, 3, 3, 3, 1, 3, 3, 1, 1, 1, 2, 2, 3, 3, 3,
       3, 3, 3, 3, 2, 0, 2, 2, 2, 3, 2, 2, 1, 1, 1, 2, 2, 1, 2, 2, 2, 3,
       3, 3, 3, 2, 3, 3, 3, 3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2,
       1, 2, 1, 1, 1, 1, 1, 3, 3, 3, 1, 1, 1, 2, 2, 2, 2, 2, 1, 1, 1, 1,
       1, 1, 1, 1, 3, 1, 3, 1, 1, 3, 3, 3, 2, 3, 3, 3, 2, 2, 3, 2, 2, 2,
       3, 2, 3, 3, 3, 2, 3, 2, 2, 3, 3, 0, 1, 1, 0, 2, 1, 0, 2, 2, 1, 1,
       1, 2, 2, 3, 1, 3, 2, 1, 1, 1, 1, 1, 2, 2, 2, 2, 1, 1, 2, 1, 1, 2,
       2, 3, 1, 1, 2, 1, 0, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 2, 4, 3,
       3, 2, 2, 2, 1, 2, 2, 3, 1, 3, 3, 3, 2, 2, 3, 3, 1, 2, 3, 1, 1, 3,
       2, 3, 3, 3, 3, 1], dtype=int32)

Create dataframe with all data including cluster number

In [58]:
kmeans.labels_.shape

(248,)

In [59]:
postcode.shape

(248, 81)

In [60]:
venue_sorted.shape

(244, 11)

In [61]:
postcode.head()

postcode                     wijk               buurt woonplaats  \
0      1011       Nieuwmarkt/Lastage    Oosterdokseiland  Amsterdam   
1      1012  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  Amsterdam   
2      1013          Haarlemmerbuurt    Westerdokseiland  Amsterdam   
3      1014    Westelijk Havengebied       Alfa-driehoek  Amsterdam   
4      1015      Grachtengordel-West    Langestraat e.o.  Amsterdam   

    gemeente      provincie   latitude  longitude  tot_inwoners   tot_0-5  \
0  Amsterdam  Noord-Holland  52.372976   4.903957        9605.0  0.030713   
1  Amsterdam  Noord-Holland  52.373386   4.894064        8245.0  0.026683   
2  Amsterdam  Noord-Holland  52.396789   4.876607       21185.0  0.052396   
3  Amsterdam  Noord-Holland  52.392305   4.855884         580.0  0.051724   
4  Amsterdam  Noord-Holland  52.379093   4.885109       14860.0  0.038694   

   tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  tot_35-40  \
0  0.030193   0.022905   0.032795   0.092140   0.114524   0.086934   0.067673   
1  0.016374   0.013948   0.019406   0.133414   0.206792   0.141298   0.084900   
2  0.040359   0.031862   0.032570   0.060892   0.097947   0.101251   0.090158   
3  0.025862   0.008621   0.025862   0.043103   0.232759   0.215517   0.103448   
4  0.031292   0.028937   0.029946   0.073015   0.108008   0.097241   0.074361   

   tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  tot_65-70  \
0   0.064029   0.067673   0.080167   0.081728   0.078084   0.069755   
1   0.066101   0.061856   0.059430   0.050940   0.040631   0.036386   
2   0.078829   0.079537   0.076941   0.069389   0.063016   0.053576   
3   0.086207   0.060345   0.043103   0.043103   0.025862   0.017241   
4   0.072342   0.083109   0.079071   0.068977   0.062248   0.070996   

   tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man  \
0   0.037480   0.020822   0.011973   0.006247   0.003644  0.001562  0.519521   
1   0.021831   0.010309   0.004851   0.001819   0.000606  0.000000  0.545179   
2   0.031626   0.018881   0.012037   0.005664   0.002360  0.000708  0.501770   
3   0.017241   0.017241   0.008621   0.000000   0.000000  0.000000  0.577586   
4   0.038022   0.024226   0.012113   0.004711   0.002355  0.000336  0.506729   

    man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  \
0  0.015096  0.014055   0.010932   0.015617   0.038522   0.053618   0.045809   
1  0.012735  0.007277   0.007277   0.007884   0.055791   0.102486   0.078229   
2  0.025490  0.021005   0.016285   0.016757   0.027614   0.044843   0.050979   
3  0.025862  0.008621   0.000000   0.017241   0.025862   0.129310   0.120690   
4  0.019179  0.015478   0.014805   0.015141   0.030283   0.049125   0.048789   

   man_35-40  man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  \
0   0.039563   0.036960   0.040083   0.047892   0.044768   0.042686   
1   0.053366   0.043663   0.038205   0.040631   0.032747   0.023651   
2   0.043899   0.042011   0.043191   0.041539   0.034930   0.031626   
3   0.060345   0.060345   0.034483   0.034483   0.034483   0.017241   
4   0.039704   0.039031   0.045087   0.043742   0.037685   0.031629   

   man_65-70  man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  \
0   0.036439   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   
1   0.020619   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   
2   0.027142   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   
3   0.008621   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   
4   0.036339   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   

   tot_vrouw  vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  \
0   0.480479   0.015617    0.015617     0.011973     0.016658     0.053618   
1   0.454215   0.014554    0.009096     0.007884     0.012129     0.078229   
2   0.498230   0.026906    0.019353     0.015577     0.015813     0.033278   
3   0.42241

In [62]:
#Insert cluster number
postcode.insert(1, 'cluster', kmeans.labels_)

#Merge postal code dataframe with sorted venues dataframe
pcdata = pd.merge(postcode, venue_sorted, on='postcode')

pcdata.head()

postcode  cluster                     wijk               buurt woonplaats  \
0      1011        3       Nieuwmarkt/Lastage    Oosterdokseiland  Amsterdam   
1      1012        3  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  Amsterdam   
2      1013        3          Haarlemmerbuurt    Westerdokseiland  Amsterdam   
3      1014        3    Westelijk Havengebied       Alfa-driehoek  Amsterdam   
4      1015        3      Grachtengordel-West    Langestraat e.o.  Amsterdam   

    gemeente      provincie   latitude  longitude  tot_inwoners   tot_0-5  \
0  Amsterdam  Noord-Holland  52.372976   4.903957        9605.0  0.030713   
1  Amsterdam  Noord-Holland  52.373386   4.894064        8245.0  0.026683   
2  Amsterdam  Noord-Holland  52.396789   4.876607       21185.0  0.052396   
3  Amsterdam  Noord-Holland  52.392305   4.855884         580.0  0.051724   
4  Amsterdam  Noord-Holland  52.379093   4.885109       14860.0  0.038694   

   tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  tot_35-40  \
0  0.030193   0.022905   0.032795   0.092140   0.114524   0.086934   0.067673   
1  0.016374   0.013948   0.019406   0.133414   0.206792   0.141298   0.084900   
2  0.040359   0.031862   0.032570   0.060892   0.097947   0.101251   0.090158   
3  0.025862   0.008621   0.025862   0.043103   0.232759   0.215517   0.103448   
4  0.031292   0.028937   0.029946   0.073015   0.108008   0.097241   0.074361   

   tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  tot_65-70  \
0   0.064029   0.067673   0.080167   0.081728   0.078084   0.069755   
1   0.066101   0.061856   0.059430   0.050940   0.040631   0.036386   
2   0.078829   0.079537   0.076941   0.069389   0.063016   0.053576   
3   0.086207   0.060345   0.043103   0.043103   0.025862   0.017241   
4   0.072342   0.083109   0.079071   0.068977   0.062248   0.070996   

   tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man  \
0   0.037480   0.020822   0.011973   0.006247   0.003644  0.001562  0.519521   
1   0.021831   0.010309   0.004851   0.001819   0.000606  0.000000  0.545179   
2   0.031626   0.018881   0.012037   0.005664   0.002360  0.000708  0.501770   
3   0.017241   0.017241   0.008621   0.000000   0.000000  0.000000  0.577586   
4   0.038022   0.024226   0.012113   0.004711   0.002355  0.000336  0.506729   

    man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  \
0  0.015096  0.014055   0.010932   0.015617   0.038522   0.053618   0.045809   
1  0.012735  0.007277   0.007277   0.007884   0.055791   0.102486   0.078229   
2  0.025490  0.021005   0.016285   0.016757   0.027614   0.044843   0.050979   
3  0.025862  0.008621   0.000000   0.017241   0.025862   0.129310   0.120690   
4  0.019179  0.015478   0.014805   0.015141   0.030283   0.049125   0.048789   

   man_35-40  man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  \
0   0.039563   0.036960   0.040083   0.047892   0.044768   0.042686   
1   0.053366   0.043663   0.038205   0.040631   0.032747   0.023651   
2   0.043899   0.042011   0.043191   0.041539   0.034930   0.031626   
3   0.060345   0.060345   0.034483   0.034483   0.034483   0.017241   
4   0.039704   0.039031   0.045087   0.043742   0.037685   0.031629   

   man_65-70  man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  \
0   0.036439   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   
1   0.020619   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   
2   0.027142   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   
3   0.008621   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   
4   0.036339   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   

   tot_vrouw  vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  \
0   0.480479   0.015617    0.015617     0.011973     0.016658     0.053618   
1   0.454215   0.014554    0.009096     0.007884     0.012129     0.078229   
2   0.498230   0.026906    0.019353

### Show maps with postcode clusters

In [63]:
# create map
map_clusters = folium.Map(location=[NL_coords[0], NL_coords[1]], zoom_start=9)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(pcdata['latitude'], pcdata['longitude'], pcdata['postcode'], pcdata['cluster']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Examine clusters

<b>Overall statistics as comparison</b>

In [64]:
pcdata.describe()

postcode     cluster    latitude   longitude  tot_inwoners  \
count   244.000000  244.000000  244.000000  244.000000    244.000000   
mean   2371.803279    2.016393   52.128215    4.673331   9068.463115   
std     956.495516    0.893356    0.176014    0.306128   5358.851337   
min    1011.000000    0.000000   51.871742    4.218229     10.000000   
25%    1090.000000    1.000000   51.962515    4.410400   6083.750000   
50%    2571.500000    2.000000   52.084516    4.551651   8852.500000   
75%    3067.250000    3.000000   52.344097    4.934455  12270.000000   
max    3585.000000    4.000000   52.423834    5.164979  25910.000000   

          tot_0-5    tot_5-10   tot_10-15   tot_15-20   tot_20-25   tot_25-30  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean     0.057986    0.050522    0.045956    0.049911    0.085078    0.098287   
std      0.022510    0.021389    0.020696    0.023884    0.053233    0.047210   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.047979    0.039184    0.034128    0.039050    0.055999    0.065315   
50%      0.058492    0.051191    0.046735    0.050149    0.075703    0.095389   
75%      0.068179    0.061704    0.056562    0.059555    0.102083    0.126483   
max      0.171053    0.120810    0.119088    0.300000    0.472550    0.300000   

        tot_30-35   tot_35-40   tot_40-45   tot_45-50   tot_50-55   tot_55-60  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean     0.089432    0.075509    0.071411    0.069742    0.064474    0.059297   
std      0.038780    0.035111    0.033078    0.021390    0.019450    0.024005   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.068219    0.064759    0.062149    0.060575    0.056466    0.048587   
50%      0.087015    0.074069    0.068963    0.067006    0.063001    0.056638   
75%      0.104606    0.083229    0.076572    0.075432    0.071718    0.065986   
max      0.333333    0.500000    0.500000    0.200000    0.166667    0.200000   

        tot_60-65   tot_65-70   tot_70-75   tot_75-80   tot_80-85   tot_85-90  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean     0.051426    0.046577    0.028881    0.022707    0.015710    0.010429   
std      0.028732    0.023553    0.013814    0.015575    0.011537    0.011751   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.040193    0.034146    0.020510    0.014752    0.008314    0.004179   
50%      0.048532    0.041566    0.026564    0.019965    0.012116    0.006646   
75%      0.058724    0.055556    0.036302    0.028357    0.020600    0.013543   
max      0.333333    0.200000    0.084034    0.166667    0.067538    0.111111   

        tot_90-95     tot_95-     tot_man     man_0-5    man_5-10   man_10-15  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean     0.004886    0.001361    0.503504    0.029738    0.025511    0.023580   
std      0.005742    0.002195    0.053701    0.012784    0.011501    0.011111   
min      0.000000    0.000000    0.445011    0.000000    0.000000    0.000000   
25%      0.001288    0.000000    0.482421    0.024803    0.019758    0.017418   
50%      0.003010    0.000703    0.495938    0.029974    0.026332    0.023528   
75%      0.006557    0.001536    0.508205    0.035929    0.031734    0.029322   
max      0.045752    0.021786    1.000000    0.111111    0.063251    0.059966   

        man_15-20   man_20-25   man_25-30   man_30-35   man_35-40   man_40-45  \
count  244.000000  244.000000  244.000000  244.000000  244.000000  244.000000   
mean     0.024617    0.039229    0.049287    0.046890    0.038752    0.040039   
std      0.011261    0.024402    0.034841    0.031990    0.017021    0.034797   
min      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
25%      0.019142    0.027249    0.0

Some key stats:
- Average inhabitants: 9068.463115
- Average percentage females: 49.9288%
- Average with migration background non-western:  31.2550%
- Average single person households: 49.9532%
- Average standardised income: 21.982787

<b>Cluster 0</b>

In [65]:
pcdata.loc[pcdata['cluster'] == 0]

postcode  cluster                   wijk                      buurt  \
23       1041        0  Westelijk Havengebied             Petroleumhaven   
24       1042        0  Westelijk Havengebied            Vervoerscentrum   
25       1043        0  Westelijk Havengebied            Westhaven Noord   
26       1046        0  Westelijk Havengebied               Amerikahaven   
27       1047        0  Westelijk Havengebied               Amerikahaven   
69       1101        0   Amstel III/Bullewijk  Amstel III deel C/D Noord   
163      3041        0                  Noord           Blijdorpsepolder   
166      3044        0              Overschie                  Overschie   
168      3047        0              Overschie                  Overschie   
201      3088        0               Charlois          Charlois Zuidrand   

             woonplaats   gemeente      provincie   latitude  longitude  \
23            Amsterdam  Amsterdam  Noord-Holland  52.414315   4.839814   
24            Amsterdam  Amsterdam  Noord-Holland  52.404253   4.824768   
25            Amsterdam  Amsterdam  Noord-Holland  52.388623   4.815402   
26            Amsterdam  Amsterdam  Noord-Holland  52.389960   4.782460   
27            Amsterdam  Amsterdam  Noord-Holland  52.409972   4.749429   
69   Amsterdam-Zuidoost  Amsterdam  Noord-Holland  52.308778   4.940660   
163           Rotterdam  Rotterdam   Zuid-Holland  51.928649   4.441546   
166           Rotterdam  Rotterdam   Zuid-Holland  51.930875   4.417564   
168           Rotterdam  Rotterdam   Zuid-Holland  51.947406   4.400721   
201           Rotterdam  Rotterdam   Zuid-Holland  51.871742   4.440550   

     tot_inwoners   tot_0-5  tot_5-10  tot_10-15  tot_15-20  tot_20-25  \
23           25.0  0.000000  0.000000   0.000000   0.000000   0.200000   
24           15.0  0.000000  0.000000   0.000000   0.000000   0.000000   
25           50.0  0.000000  0.000000   0.000000   0.000000   0.000000   
26           35.0  0.000000  0.000000   0.000000   0.000000   0.142857   
27           30.0  0.166667  0.000000   0.000000   0.000000   0.166667   
69          135.0  0.037037  0.000000   0.000000   0.000000   0.148148   
163         135.0  0.000000  0.037037   0.037037   0.037037   0.148148   
166         105.0  0.047619  0.000000   0.000000   0.000000   0.047619   
168          80.0  0.062500  0.062500   0.000000   0.062500   0.062500   
201          25.0  0.000000  0.000000   0.000000   0.000000   0.000000   

     tot_25-30  tot_30-35  tot_35-40  tot_40-45  tot_45-50  tot_50-55  \
23    0.200000   0.200000   0.200000   0.000000   0.000000   0.000000   
24    0.000000   0.333333   0.000000   0.000000   0.000000   0.000000   
25    0.300000   0.200000   0.100000   0.100000   0.100000   0.100000   
26    0.142857   0.142857   0.000000   0.142857   0.142857   0.000000   
27    0.166667   0.000000   0.000000   0.000000   0.166667   0.166667   
69    0.296296   0.259259   0.148148   0.074074   0.000000   0.037037   
163   0.111111   0.148148   0.111111   0.074074   0.111111   0.111111   
166   0.000000   0.047619   0.047619   0.095238   0.095238   0.047619   
168   0.062500   0.062500   0.062500   0.000000   0.000000   0.062500   
201   0.200000   0.200000   0.000000   0.000000   0.200000   0.000000   

     tot_55-60  tot_60-65  tot_65-70  tot_70-75  tot_75-80  tot_80-85  \
23    0.200000   0.200000   0.200000   0.000000   0.000000        0.0   
24    0.000000   0.333333   0.000000   0.000000   0.000000        0.0   
25    0.100000   0.000000   0.000000   0.000000   0.000000        0.0   
26    0.000000   0.142857   0.000000   0.000000   0.000000        0.0   
27    0.166667   0.000000   0.166667   0.000000   0.166667        0.0   
69    0.037037   0.037037   0.000000   0.000000   0.000000        0.0   
163   0.037037   0.074074   0.037037   0.037037   0.000000        0.0   
166   0.095238   0.142857   0.095238   0.047619   0.000000        0.0   
168   0.187500   0.125000   0.000000   0.062500   0.000000        

In [66]:
pcdata.loc[pcdata['cluster'] == 0].describe()

postcode  cluster   latitude  longitude  tot_inwoners    tot_0-5  \
count    10.000000     10.0  10.000000  10.000000     10.000000  10.000000   
mean   1854.000000      0.0  52.199457   4.665291     63.500000   0.031382   
std    1033.883187      0.0   0.243322   0.212654     46.729125   0.053203   
min    1041.000000      0.0  51.871742   4.400721     15.000000   0.000000   
25%    1043.750000      0.0  51.935008   4.440799     26.250000   0.000000   
50%    1074.000000      0.0  52.348700   4.765944     42.500000   0.000000   
75%    3043.250000      0.0  52.400680   4.822426     98.750000   0.044974   
max    3088.000000      0.0  52.414315   4.940660    135.000000   0.166667   

        tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  \
count  10.000000  10.000000  10.000000  10.000000  10.000000  10.000000   
mean    0.009954   0.003704   0.009954   0.091594   0.147943   0.159372   
std     0.021826   0.011712   0.021826   0.077718   0.107164   0.101578   
min     0.000000   0.000000   0.000000   0.000000   0.000000   0.000000   
25%     0.000000   0.000000   0.000000   0.011905   0.074653   0.082589   
50%     0.000000   0.000000   0.000000   0.102679   0.154762   0.174074   
75%     0.000000   0.000000   0.000000   0.148148   0.200000   0.200000   
max     0.062500   0.037037   0.062500   0.200000   0.300000   0.333333   

       tot_35-40  tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  \
count  10.000000  10.000000  10.000000  10.000000  10.000000  10.000000   
mean    0.066938   0.048624   0.081587   0.052493   0.102348   0.105516   
std     0.071228   0.054578   0.076766   0.057844   0.081648   0.107018   
min     0.000000   0.000000   0.000000   0.000000   0.000000   0.000000   
25%     0.000000   0.000000   0.000000   0.000000   0.037037   0.009259   
50%     0.055060   0.037037   0.097619   0.042328   0.097619   0.099537   
75%     0.108333   0.089947   0.134921   0.090625   0.182292   0.142857   
max     0.200000   0.142857   0.200000   0.166667   0.200000   0.333333   

       tot_65-70  tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95  \
count  10.000000  10.000000  10.000000       10.0  10.000000       10.0   
mean    0.049894   0.014716   0.016667        0.0   0.004762        0.0   
std     0.076974   0.024450   0.052705        0.0   0.015058        0.0   
min     0.000000   0.000000   0.000000        0.0   0.000000        0.0   
25%     0.000000   0.000000   0.000000        0.0   0.000000        0.0   
50%     0.000000   0.000000   0.000000        0.0   0.000000        0.0   
75%     0.080688   0.027778   0.000000        0.0   0.000000        0.0   
max     0.200000   0.062500   0.166667        0.0   0.047619        0.0   

       tot_95-    tot_man    man_0-5   man_5-10  man_10-15  man_15-20  \
count     10.0  10.000000  10.000000  10.000000       10.0  10.000000   
mean       0.0   0.684339   0.003704   0.003704        0.0   0.004762   
std        0.0   0.166842   0.011712   0.011712        0.0   0.015058   
min        0.0   0.500000   0.000000   0.000000        0.0   0.000000   
25%        0.0   0.578571   0.000000   0.000000        0.0   0.000000   
50%        0.0   0.633333   0.000000   0.000000        0.0   0.000000   
75%        0.0   0.777778   0.000000   0.000000        0.0   0.000000   
max        0.0   1.000000   0.037037   0.037037        0.0   0.047619   

       man_20-25  man_25-30  man_30-35  man_35-40  man_40-45  man_45-50  \
count  10.000000  10.000000  10.000000  10.000000  10.000000  10.000000   
mean    0.032222   0.113499   0.138307   0.062017   0.077837   0.038790   
std     0.051971   0.129733   0.103705   0.062008   0.072598   0.053504   
min     0.000000   0.000000   0.000000   0.000000   0.000000   0.000000   
25%     0.000000   0.000000   0.063492   0.000000   0.009259   0.000000   
50%     0.000000   0.068287   0.145503   0.068287   0.068287   0.018519   
75%     0.075000   0.202381   0.200000   0.093519   0.130952   0.058780   
max     0.111111   0.

Key stats:
- Average inhabitants: 63.500000
- Average percentage females: 32.5661%
- Average with migration background non-western:  22.0694%
- Average single person households: 59.8779%
- Average standardised income: 0.0

Analysis:
- Almost no inhabitants, almost no income.
- Venues include mostly harbor/marina, snack places and leasure zones
- See also map and area names: industrial and harbour area

Conclusion:
- Cluster is harbour area. Not suited for settling our salad bar

<b>Cluster 1</b>

In [67]:
pcdata.loc[pcdata['cluster'] == 1]

postcode  cluster                               wijk  \
11       1023        1         Noordelijke IJ-oevers Oost   
13       1025        1                 IJplein/Vogelbuurt   
14       1026        1                          Waterland   
15       1027        1                          Waterland   
17       1032        1                          Volewijck   
18       1033        1         Noordelijke IJ-oevers West   
20       1035        1                      Oostzanerwerf   
22       1037        1                      Oostzanerwerf   
45       1068        1                  Lutkemeer/Ookmeer   
47       1071        1                        Vondelbuurt   
53       1077        1                       Stadionbuurt   
56       1081        1                             Zuidas   
57       1082        1                             Zuidas   
58       1083        1                             Zuidas   
76       1108        1                         Nellestein   
77       1109        1                           Driemond   
78       2491        1              Wijk 44 Leidschenveen   
81       2495        1                  Wijk 41 Hoornwijk   
105      2544        1                Wijk 34 Morgenstond   
108      2547        1                  Wijk 32 Leyenburg   
110      2551        1                 Wijk 17 Loosduinen   
111      2552        1                 Wijk 17 Loosduinen   
112      2553        1                 Wijk 17 Loosduinen   
113      2554        1     Wijk 15 Kijkduin en Ockenburgh   
114      2555        1                    Wijk 18 Waldeck   
118      2564        1     Wijk 12 Bomen- en Bloemenbuurt   
119      2565        1     Wijk 12 Bomen- en Bloemenbuurt   
120      2566        1     Wijk 12 Bomen- en Bloemenbuurt   
126      2582        1                   Wijk 11 Duinoord   
127      2583        1  Wijk 09 Geuzen- en Statenkwartier   
128      2584        1              Wijk 05 Archipelbuurt   
129      2585        1                Wijk 23 Willemspark   
130      2586        1               Wijk 07 Scheveningen   
131      2587        1               Wijk 07 Scheveningen   
132      2591        1       Wijk 25 Mariahoeve en Marlot   
133      2592        1       Wijk 25 Mariahoeve en Marlot   
135      2594        1              Wijk 27 Stationsbuurt   
137      2596        1                 Wijk 24 Haagse Bos   
138      2597        1              Wijk 02 Belgisch Park   
164      3042        1                          Overschie   
165      3043        1                          Overschie   
171      3053        1           Hillegersberg-Schiebroek   
172      3054        1           Hillegersberg-Schiebroek   
173      3055        1           Hillegersberg-Schiebroek   
177      3062        1                Kralingen-Crooswijk   
180      3065        1                    Prins Alexander   
181      3066        1                    Prins Alexander   
182      3067        1                    Prins Alexander   
183      3068        1                    Prins Alexander   
184      3069        1                    Prins Alexander   
189      3075        1                         Feijenoord   
190      3076        1                        IJsselmonde   
192      3078        1                        IJsselmonde   
193      3079        1                        IJsselmonde   
197      3084        1                           Charlois   
198      3085        1                           Charlois   
200      3087        1                           Charlois   
202      3089        1                           Charlois   
221      3542        1                       Wijk 01 West   
224      3546        1           Wijk 10 Vleuten-De Meern   
232      3563        1                  Wijk 03 Overvecht   
235      3566        1                  Wijk 04 Noordoost   
236      3571        1                  Wijk 04 Noordoost   
243      3585        1                       Wijk 05 Oost   

                                  buurt

In [68]:
pcdata.loc[pcdata['cluster'] == 1].describe()

postcode  cluster   latitude  longitude  tot_inwoners    tot_0-5  \
count    64.000000     64.0  64.000000  64.000000     64.000000  64.000000   
mean   2431.265625      1.0  52.106000   4.583926   7884.453125   0.050728   
std     854.873002      0.0   0.170598   0.299901   5288.295110   0.014897   
min    1023.000000      1.0  51.873795   4.218229    130.000000   0.000000   
25%    2145.500000      1.0  51.958935   4.311830   4223.750000   0.045883   
50%    2585.500000      1.0  52.078680   4.507072   7800.000000   0.052625   
75%    3067.250000      1.0  52.167492   4.883003  11053.750000   0.060113   
max    3585.000000      1.0  52.423834   5.148921  22325.000000   0.071429   

        tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  \
count  64.000000  64.000000  64.000000  64.000000  64.000000  64.000000   
mean    0.052353   0.051149   0.051531   0.056957   0.059767   0.058280   
std     0.012604   0.013719   0.012639   0.025814   0.021668   0.019944   
min     0.026144   0.024357   0.025822   0.000000   0.017188   0.000000   
25%     0.044690   0.041883   0.042632   0.043069   0.045863   0.047964   
50%     0.051942   0.049695   0.051544   0.053469   0.061941   0.058160   
75%     0.058031   0.055966   0.057458   0.066707   0.074381   0.073104   
max     0.083595   0.093023   0.090134   0.145499   0.125846   0.108707   

       tot_35-40  tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  \
count  64.000000  64.000000  64.000000  64.000000  64.000000  64.000000   
mean    0.058132   0.065482   0.071894   0.073860   0.070198   0.065083   
std     0.014596   0.011813   0.014677   0.016142   0.014207   0.016762   
min     0.000000   0.027778   0.049391   0.043302   0.045332   0.036723   
25%     0.051293   0.058127   0.061568   0.061912   0.061640   0.055393   
50%     0.059462   0.063290   0.067641   0.070655   0.067866   0.063444   
75%     0.068589   0.071779   0.077997   0.082770   0.077760   0.071461   
max     0.080523   0.093750   0.140351   0.125000   0.115385   0.153846   

       tot_65-70  tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95  \
count  64.000000  64.000000  64.000000  64.000000  64.000000  64.000000   
mean    0.067106   0.044874   0.037289   0.030418   0.020116   0.010680   
std     0.016771   0.011528   0.011716   0.011143   0.012256   0.007903   
min     0.037429   0.023256   0.000000   0.009709   0.000000   0.000000   
25%     0.055311   0.037911   0.030300   0.023420   0.013067   0.006173   
50%     0.064276   0.042783   0.035874   0.029168   0.019513   0.009680   
75%     0.075034   0.050997   0.043576   0.036547   0.025990   0.014923   
max     0.117647   0.084034   0.075964   0.067538   0.067538   0.045752   

         tot_95-    tot_man    man_0-5   man_5-10  man_10-15  man_15-20  \
count  64.000000  64.000000  64.000000  64.000000  64.000000  64.000000   
mean    0.003120   0.486731   0.026126   0.026008   0.026721   0.026306   
std     0.003455   0.026069   0.008336   0.008256   0.007063   0.007964   
min     0.000000   0.445011   0.000000   0.000000   0.013532   0.000000   
25%     0.000908   0.471282   0.023428   0.022575   0.022721   0.021825   
50%     0.002503   0.481772   0.027491   0.027012   0.026209   0.026198   
75%     0.004549   0.491020   0.031323   0.030160   0.029427   0.030856   
max     0.021786   0.593750   0.039203   0.048544   0.052632   0.057143   

       man_20-25  man_25-30  man_30-35  man_35-40  man_40-45  man_45-50  \
count  64.000000  64.000000  64.000000  64.000000  64.000000  64.000000   
mean    0.028698   0.029545   0.028491   0.028386   0.031688   0.035666   
std     0.015779   0.012324   0.010488   0.008721   0.005050   0.009038   
min     0.000000   0.000000   0.000000   0.000000   0.019621   0.023256   
25%     0.019586   0.021739   0.024050   0.025816   0.028339   0.031144   
50%     0.027247   0.030186   0.028344   0.028458   0.031250   0.033559   
75%     0.032917   0.036794   0.034316   0.033805   0.035131   0.037966   
max

Key stats:
- Average inhabitants: 7884.453125
- Average percentage females: 51,4327%
- Average with migration background non-western:  19,4456%
- Average single person households: 45,2300%
- Average standardised income: 25.329687
    
Analysis:
- High population density
- Lower than average non-western migration
- Higher than average income
- Venues mostly leasure, sport and shopping

Conclusion:
- Cluster is residential zone, few restaurants. Not ideal for a salad bar, although it has a high average income and relatively many females.

<b>Cluster 2</b>

In [69]:
pcdata.loc[pcdata['cluster'] == 2]

postcode  cluster                               wijk  \
8        1019        2       Oostelijke Eilanden/Kadijken   
9        1021        2                 IJplein/Vogelbuurt   
10       1022        2                 IJplein/Vogelbuurt   
12       1024        2                Waterlandpleinbuurt   
16       1031        2                          Volewijck   
19       1034        2   Nieuwendammerdijk/Buiksloterdijk   
21       1036        2                  Tuindorp Oostzaan   
37       1060        2                  Lutkemeer/Ookmeer   
38       1061        2                        De Kolenkit   
40       1063        2               Slotermeer-Noordoost   
41       1064        2                  Slotervaart Noord   
42       1065        2                  Slotervaart Noord   
43       1066        2                   Slotervaart Zuid   
44       1067        2                         Geuzenveld   
46       1069        2          Middelveldsche Akerpolder   
59       1086        2                        IJburg West   
60       1087        2                        IJburg West   
68       1098        2                         Middenmeer   
70       1102        2            Bijlmer Centrum (D,F,H)   
71       1103        2               Bijlmer Oost (E,G,K)   
72       1104        2               Bijlmer Oost (E,G,K)   
74       1106        2            Bijlmer Centrum (D,F,H)   
75       1107        2             Holendrecht/Reigersbos   
79       2492        2              Wijk 44 Leidschenveen   
80       2493        2              Wijk 44 Leidschenveen   
82       2496        2                  Wijk 41 Hoornwijk   
83       2497        2                  Wijk 41 Hoornwijk   
84       2498        2                   Wijk 42 Ypenburg   
89       2515        2              Wijk 27 Stationsbuurt   
94       2522        2  Wijk 38 Laakkwartier en Spoorwijk   
95       2523        2  Wijk 38 Laakkwartier en Spoorwijk   
96       2524        2  Wijk 38 Laakkwartier en Spoorwijk   
97       2525        2              Wijk 27 Stationsbuurt   
98       2526        2              Wijk 27 Stationsbuurt   
99       2531        2                   Wijk 36 Moerwijk   
100      2532        2                   Wijk 36 Moerwijk   
101      2533        2                   Wijk 36 Moerwijk   
102      2541        2                   Wijk 36 Moerwijk   
103      2542        2                Wijk 34 Morgenstond   
104      2543        2      Wijk 33 Bouwlust en Vrederust   
106      2545        2                Wijk 34 Morgenstond   
107      2546        2                    Wijk 28 Centrum   
109      2548        2            Wijk 40 Wateringse Veld   
121      2571        2             Wijk 29 Schildersbuurt   
122      2572        2          Wijk 30 Transvaalkwartier   
123      2573        2    Wijk 31 Rustenburg en Oostbroek   
124      2574        2                  Wijk 32 Leyenburg   
125      2581        2  Wijk 09 Geuzen- en Statenkwartier   
142      3014        2                  Rotterdam Centrum   
146      3022        2                         Delfshaven   
147      3023        2                         Delfshaven   
149      3025        2                         Delfshaven   
150      3026        2                         Delfshaven   
151      3027        2                         Delfshaven   
153      3029        2                         Delfshaven   
157      3034        2                Kralingen-Crooswijk   
159      3036        2                              Noord   
160      3037        2                              Noord   
167      3045        2                              Noord   
169      3051        2           Hillegersberg-Schiebroek   
170      3052        2           Hillegersberg-Schiebroek   
174      3056        2           Hillegersberg-Schiebroek   
175      3059        2                    Prins Alexander   
179      3064        2                    Prins Alexander   
185      3071        2                  

In [70]:
pcdata.loc[pcdata['cluster'] == 2].describe()

postcode  cluster   latitude  longitude  tot_inwoners    tot_0-5  \
count    83.000000     83.0  83.000000  83.000000     83.000000  83.000000   
mean   2410.204819      2.0  52.105703   4.627404  10401.506024   0.074242   
std     897.550919      0.0   0.171962   0.298188   5230.742598   0.018195   
min    1019.000000      2.0  51.874654   4.261203   1355.000000   0.049096   
25%    1105.000000      2.0  51.950578   4.367265   7012.500000   0.063720   
50%    2546.000000      2.0  52.061080   4.495865  10220.000000   0.070725   
75%    3057.500000      2.0  52.307115   4.934353  13285.000000   0.082025   
max    3573.000000      2.0  52.407689   5.148243  25910.000000   0.171053   

        tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  \
count  83.000000  83.000000  83.000000  83.000000  83.000000  83.000000   
mean    0.068439   0.062109   0.059810   0.072192   0.083469   0.084252   
std     0.016739   0.015756   0.011742   0.024088   0.025645   0.020942   
min     0.044053   0.041929   0.033543   0.018868   0.018581   0.029561   
25%     0.059003   0.051507   0.052316   0.057825   0.070681   0.073532   
50%     0.063267   0.057409   0.059198   0.073135   0.085255   0.085402   
75%     0.072279   0.067034   0.066602   0.087667   0.100336   0.092420   
max     0.120810   0.119088   0.089928   0.129047   0.157895   0.203947   

       tot_35-40  tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  \
count  83.000000  83.000000  83.000000  83.000000  83.000000  83.000000   
mean    0.078406   0.076876   0.074535   0.067320   0.055267   0.043185   
std     0.014318   0.016461   0.015939   0.013703   0.014091   0.012606   
min     0.053824   0.057206   0.035088   0.024123   0.015351   0.006579   
25%     0.069390   0.065910   0.065384   0.060315   0.047608   0.036871   
50%     0.075308   0.071312   0.070961   0.064662   0.054264   0.042628   
75%     0.081016   0.082060   0.077449   0.072133   0.061794   0.050017   
max     0.120177   0.128049   0.128378   0.111601   0.108664   0.079773   

       tot_65-70  tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95  \
count  83.000000  83.000000  83.000000  83.000000  83.000000  83.000000   
mean    0.036614   0.022943   0.017768   0.011509   0.006992   0.003237   
std     0.009772   0.006712   0.006330   0.005838   0.004961   0.002862   
min     0.008772   0.004386   0.000000   0.000000   0.000000   0.000000   
25%     0.032410   0.019206   0.013864   0.007476   0.003699   0.001407   
50%     0.036840   0.023760   0.017724   0.011291   0.005643   0.002465   
75%     0.042135   0.026768   0.022623   0.014712   0.008823   0.004431   
max     0.059285   0.037900   0.029808   0.026908   0.024462   0.013699   

         tot_95-    tot_man    man_0-5   man_5-10  man_10-15  man_15-20  \
count  83.000000  83.000000  83.000000  83.000000  83.000000  83.000000   
mean    0.000845   0.499965   0.038276   0.034964   0.032068   0.030206   
std     0.001096   0.011715   0.009599   0.008789   0.008602   0.006168   
min     0.000000   0.463942   0.024548   0.021964   0.017544   0.015351   
25%     0.000000   0.493263   0.032366   0.029965   0.026370   0.025951   
50%     0.000646   0.500333   0.036945   0.032738   0.029641   0.029729   
75%     0.001122   0.507304   0.042522   0.037126   0.034348   0.034038   
max     0.006289   0.525963   0.089912   0.063251   0.059966   0.045782   

       man_20-25  man_25-30  man_30-35  man_35-40  man_40-45  man_45-50  \
count  83.000000  83.000000  83.000000  83.000000  83.000000  83.000000   
mean    0.035540   0.040411   0.041191   0.038993   0.038913   0.038798   
std     0.011527   0.012849   0.011084   0.007622   0.007879   0.007872   
min     0.006579   0.009291   0.009291   0.022663   0.026423   0.021930   
25%     0.028637   0.033789   0.035081   0.034226   0.032841   0.033560   
50%     0.035590   0.040876   0.041196   0.037841   0.037238   0.038246   
75%     0.042433   0.049333   0.046341   0.042583   0.042702   0.041667   
max

Key stats:
- Average inhabitants: 10401.506024
- Average percentage females: 50.0095%
- Average with migration background non-western: 45,9970%
- Average single person households: 41,8285%
- Average standardised income: 21.854217

Analysis:
- Very high population density
- Relatively high migration background, higher than average income, but lower than cluster 1.
- Venues inludes many restaurants

Conclusion:
- Cluster is densily populated city area with many restaurants.  Very good candidate for opening salad bar.

<b>Cluster 3</b>

In [71]:
pcdata.loc[pcdata['cluster'] == 3]

postcode  cluster                          wijk  \
0        1011        3            Nieuwmarkt/Lastage   
1        1012        3       Burgwallen-Nieuwe Zijde   
2        1013        3               Haarlemmerbuurt   
3        1014        3         Westelijk Havengebied   
4        1015        3           Grachtengordel-West   
5        1016        3       Burgwallen-Nieuwe Zijde   
6        1017        3           Grachtengordel-Zuid   
7        1018        3  Oostelijke Eilanden/Kadijken   
28       1051        3             Staatsliedenbuurt   
29       1052        3             Staatsliedenbuurt   
30       1053        3                 Da Costabuurt   
31       1054        3                Centrale Markt   
32       1055        3                      Landlust   
33       1056        3                      Landlust   
34       1057        3                 Hoofdweg e.o.   
35       1058        3               Overtoomse Veld   
36       1059        3                Westlandgracht   
39       1062        3               Overtoomse Veld   
48       1072        3                     Oude Pijp   
49       1073        3                     Oude Pijp   
50       1074        3                     Oude Pijp   
51       1075        3              Overtoomse Sluis   
52       1076        3                  Stadionbuurt   
54       1078        3                Museumkwartier   
55       1079        3                  Scheldebuurt   
61       1091        3               Oosterparkbuurt   
62       1092        3               Oosterparkbuurt   
63       1093        3                   Dapperbuurt   
64       1094        3           Indische Buurt West   
65       1095        3   Zeeburgereiland/Nieuwe Diep   
66       1096        3              Omval/Overamstel   
67       1097        3              Omval/Overamstel   
73       1105        3          Amstel III/Bullewijk   
85       2511        3               Wijk 28 Centrum   
86       2512        3               Wijk 28 Centrum   
87       2513        3              Wijk 42 Ypenburg   
88       2514        3               Wijk 28 Centrum   
90       2516        3         Wijk 27 Stationsbuurt   
91       2517        3     Wijk 22 Zeeheldenkwartier   
92       2518        3     Wijk 22 Zeeheldenkwartier   
93       2521        3         Wijk 27 Stationsbuurt   
115      2561        3    Wijk 21 Regentessekwartier   
116      2562        3              Wijk 11 Duinoord   
117      2563        3              Wijk 11 Duinoord   
134      2593        3          Wijk 26 Bezuidenhout   
136      2595        3         Wijk 27 Stationsbuurt   
139      3011        3             Rotterdam Centrum   
140      3012        3             Rotterdam Centrum   
141      3013        3             Rotterdam Centrum   
143      3015        3             Rotterdam Centrum   
144      3016        3             Rotterdam Centrum   
145      3021        3             Rotterdam Centrum   
148      3024        3                    Delfshaven   
152      3028        3                    Delfshaven   
154      3031        3           Kralingen-Crooswijk   
155      3032        3             Rotterdam Centrum   
156      3033        3                         Noord   
158      3035        3                         Noord   
161      3038        3                         Noord   
162      3039        3             Rotterdam Centrum   
176      3061        3           Kralingen-Crooswijk   
178      3063        3           Kralingen-Crooswijk   
196      3083        3                    Feijenoord   
203      3511        3            Wijk 06 Binnenstad   
204      3512        3            Wijk 06 Binnenstad   
205      3513        3            Wijk 06 Binnenstad   
206      3514        3             Wijk 04 Noordoost   
207      3515        3             Wijk 04 Noordoost   
208      3521        3            Wijk 06 Binnenstad   
209      3522        3              Wijk 08 Zuidwest   
210      3523        3       

In [72]:
pcdata.loc[pcdata['cluster'] == 3].describe()

postcode  cluster   latitude  longitude  tot_inwoners    tot_0-5  \
count    86.000000     86.0  86.000000  86.000000     86.000000  86.000000   
mean   2337.255814      3.0  52.158884   4.780368   9815.465116   0.051467   
std    1063.442116      0.0   0.172467   0.298392   4595.002889   0.014197   
min    1011.000000      3.0  51.887200   4.268899     45.000000   0.000000   
25%    1075.250000      3.0  52.070407   4.474178   7208.750000   0.045615   
50%    2562.500000      3.0  52.096694   4.875678   9282.500000   0.052116   
75%    3511.750000      3.0  52.353118   5.087860  12680.000000   0.060283   
max    3584.000000      3.0  52.396789   5.164979  21185.000000   0.076652   

        tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  \
count  86.000000  86.000000  86.000000  86.000000  86.000000  86.000000   
mean    0.037172   0.031950   0.044379   0.118673   0.136624   0.110522   
std     0.012225   0.011072   0.031355   0.066472   0.030838   0.024749   
min     0.000000   0.000000   0.000000   0.043103   0.033333   0.030577   
25%     0.030274   0.024142   0.032233   0.084447   0.114676   0.098290   
50%     0.039309   0.033825   0.039827   0.102328   0.133379   0.108803   
75%     0.046177   0.040888   0.049250   0.130797   0.148284   0.125610   
max     0.057456   0.053509   0.300000   0.472550   0.232759   0.215517   

       tot_35-40  tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  \
count  86.000000  86.000000  86.000000  86.000000  86.000000  86.000000   
mean    0.081706   0.068215   0.062949   0.056884   0.050758   0.043524   
std     0.015114   0.012639   0.011532   0.012434   0.012721   0.011855   
min     0.019458   0.020153   0.025017   0.000000   0.000000   0.000000   
25%     0.072359   0.062555   0.057345   0.051336   0.044628   0.036419   
50%     0.081198   0.069984   0.063093   0.057221   0.051003   0.045053   
75%     0.091862   0.075030   0.068230   0.064195   0.057262   0.049833   
max     0.112676   0.111111   0.111111   0.080167   0.081728   0.078084   

       tot_65-70  tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95  \
count  86.000000  86.000000  86.000000  86.000000  86.000000  86.000000   
mean    0.041070   0.024694   0.017588   0.010829   0.007319   0.002790   
std     0.013648   0.007880   0.006177   0.004411   0.011775   0.002145   
min     0.016667   0.000000   0.000000   0.000000   0.000000   0.000000   
25%     0.031760   0.019481   0.014397   0.008196   0.004013   0.001268   
50%     0.039393   0.024170   0.016825   0.010230   0.005545   0.002171   
75%     0.047383   0.029723   0.021367   0.012629   0.007569   0.003652   
max     0.111111   0.050613   0.039079   0.023726   0.111111   0.009125   

         tot_95-    tot_man    man_0-5   man_5-10  man_10-15  man_15-20  \
count  86.000000  86.000000  86.000000  86.000000  86.000000  86.000000   
mean    0.000724   0.498415   0.027560   0.018850   0.016067   0.020560   
std     0.000724   0.023735   0.011678   0.006528   0.006142   0.012328   
min     0.000000   0.460884   0.000000   0.000000   0.000000   0.000000   
25%     0.000000   0.483611   0.023399   0.015313   0.012554   0.015177   
50%     0.000633   0.497142   0.027028   0.019786   0.017042   0.019317   
75%     0.001079   0.508985   0.031424   0.023548   0.020559   0.023461   
max     0.003455   0.577586   0.111111   0.029946   0.027632   0.116667   

       man_20-25  man_25-30  man_30-35  man_35-40  man_40-45  man_45-50  \
count  86.000000  86.000000  86.000000  86.000000  86.000000  86.000000   
mean    0.051898   0.065652   0.055999   0.043978   0.037599   0.033393   
std     0.028646   0.016166   0.014395   0.010901   0.010390   0.006944   
min     0.022031   0.016667   0.000000   0.010424   0.009729   0.000000   
25%     0.036333   0.056828   0.048926   0.038015   0.032161   0.030009   
50%     0.045653   0.062941   0.054938   0.042616   0.037811   0.034056   
75%     0.056317   0.072340   0.063472   0.048995   0.040978   0.037182   
max

Key stats:
- Average inhabitants: 9815.465116
- Average percentage females: 50,1683%
- Average with migration background non-western: 26,6659%
- Average single person households: 60.7361%
- Average standardised income: 22.427907

Analysis:
- Polulation density higher than average, but slightly lower than cluster 2
- Relatively low migration background, higher than average income and higher than cluster 2, but lower than cluster 1.
- Venues inludes shops and many restaurants
- Very many single person households
- City centers

Conclusion:
Busy area with many restaurants. Very high on single person households. Very good candidate for opening salad bar.

<b>Cluster 4</b>

In [73]:
pcdata.loc[pcdata['cluster'] == 4]

postcode  cluster                   wijk                      buurt  \
215      3528        4  Wijk 09 Leidsche Rijn  Bedrijvengebied Papendorp   

    woonplaats gemeente provincie   latitude  longitude  tot_inwoners  \
215    Utrecht  Utrecht   Utrecht  52.068572   5.082438          10.0   

     tot_0-5  tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  \
215      0.0       0.0        0.0        0.0        0.0        0.0        0.0   

     tot_35-40  tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  \
215        0.5        0.5        0.0        0.0        0.0        0.0   

     tot_65-70  tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95  \
215        0.0        0.0        0.0        0.0        0.0        0.0   

     tot_95-  tot_man  man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  \
215      0.0      0.5      0.0       0.0        0.0        0.0        0.0   

     man_25-30  man_30-35  man_35-40  man_40-45  man_45-50  man_50-55  \
215        0.0        0.0        0.0        0.5        0.0        0.0   

     man_55-60  man_60-65  man_65-70  man_70-75  man_75-80  man_80-85  \
215        0.0        0.0        0.0        0.0        0.0        0.0   

     man_85-90  man_90-95  man_95-  tot_vrouw  vrouw_0-5  vrouw_5-10  \
215        0.0        0.0      0.0        1.0        0.0         0.0   

     vrouw_10-15  vrouw_15-20  vrouw_20-25  vrouw_25-30  vrouw_30-35  \
215          0.5          0.0          0.0          0.0          0.0   

     vrouw_35-40  vrouw_40-45  vrouw_45-50  vrouw_50-55  vrouw_55-60  \
215          0.0          0.0          0.5          0.0          0.0   

     vrouw_60-65  vrouw_65-70  vrouw_70-75  vrouw_75-80  vrouw_80-85  \
215          0.0          0.0          0.0          0.0          0.0   

     vrouw_85-90  vrouw_90-95  vrouw_95-  tot_allochtoon  allochtoon_westers  \
215          0.0          0.0        0.0             0.5                 0.5   

     allochtoon_nietwesters  tot_huishoudens  eenspersoons  \
215                     0.5             10.0           0.0   

     meer_zonder_kinderen  meer_met_kinderen  gem_huish_grootte  gem_inkomen  \
215                   0.0                0.5               1.86          0.0   

     std_inkomen 1st Most Common Venue 2nd Most Common Venue  \
215          0.0                 Hotel             Cafeteria   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
215             Brasserie  Fast Food Restaurant           Film Studio   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
215     Fish & Chips Shop           Fish Market           Flea Market   

    9th Most Common Venue 10th Most Common Venue  
215           Flower Shop      Fondue Restaurant

In [74]:
pcdata.loc[pcdata['cluster'] == 4].describe()

postcode  cluster   latitude  longitude  tot_inwoners  tot_0-5  \
count       1.0      1.0   1.000000   1.000000           1.0      1.0   
mean     3528.0      4.0  52.068572   5.082438          10.0      0.0   
std         NaN      NaN        NaN        NaN           NaN      NaN   
min      3528.0      4.0  52.068572   5.082438          10.0      0.0   
25%      3528.0      4.0  52.068572   5.082438          10.0      0.0   
50%      3528.0      4.0  52.068572   5.082438          10.0      0.0   
75%      3528.0      4.0  52.068572   5.082438          10.0      0.0   
max      3528.0      4.0  52.068572   5.082438          10.0      0.0   

       tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  \
count       1.0        1.0        1.0        1.0        1.0        1.0   
mean        0.0        0.0        0.0        0.0        0.0        0.0   
std         NaN        NaN        NaN        NaN        NaN        NaN   
min         0.0        0.0        0.0        0.0        0.0        0.0   
25%         0.0        0.0        0.0        0.0        0.0        0.0   
50%         0.0        0.0        0.0        0.0        0.0        0.0   
75%         0.0        0.0        0.0        0.0        0.0        0.0   
max         0.0        0.0        0.0        0.0        0.0        0.0   

       tot_35-40  tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  \
count        1.0        1.0        1.0        1.0        1.0        1.0   
mean         0.5        0.5        0.0        0.0        0.0        0.0   
std          NaN        NaN        NaN        NaN        NaN        NaN   
min          0.5        0.5        0.0        0.0        0.0        0.0   
25%          0.5        0.5        0.0        0.0        0.0        0.0   
50%          0.5        0.5        0.0        0.0        0.0        0.0   
75%          0.5        0.5        0.0        0.0        0.0        0.0   
max          0.5        0.5        0.0        0.0        0.0        0.0   

       tot_65-70  tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95  \
count        1.0        1.0        1.0        1.0        1.0        1.0   
mean         0.0        0.0        0.0        0.0        0.0        0.0   
std          NaN        NaN        NaN        NaN        NaN        NaN   
min          0.0        0.0        0.0        0.0        0.0        0.0   
25%          0.0        0.0        0.0        0.0        0.0        0.0   
50%          0.0        0.0        0.0        0.0        0.0        0.0   
75%          0.0        0.0        0.0        0.0        0.0        0.0   
max          0.0        0.0        0.0        0.0        0.0        0.0   

       tot_95-  tot_man  man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  \
count      1.0      1.0      1.0       1.0        1.0        1.0        1.0   
mean       0.0      0.5      0.0       0.0        0.0        0.0        0.0   
std        NaN      NaN      NaN       NaN        NaN        NaN        NaN   
min        0.0      0.5      0.0       0.0        0.0        0.0        0.0   
25%        0.0      0.5      0.0       0.0        0.0        0.0        0.0   
50%        0.0      0.5      0.0       0.0        0.0        0.0        0.0   
75%        0.0      0.5      0.0       0.0        0.0        0.0        0.0   
max        0.0      0.5      0.0       0.0        0.0        0.0        0.0   

       man_25-30  man_30-35  man_35-40  man_40-45  man_45-50  man_50-55  \
count        1.0        1.0        1.0        1.0        1.0        1.0   
mean         0.0        0.0        0.0        0.5        0.0        0.0   
std          NaN        NaN        NaN        NaN        NaN        NaN   
min          0.0        0.0        0.0        0.5        0.0        0.0   
25%          0.0        0.0        0.0        0.5        0.0        0.0   
50%          0.0        0.0        0.0        0.5        0.0        0.0   
75%          0.0        0.0        0.0        0.5        0.0        0.0   
max          0.0  

Key stats:
- Stats do not say much given very low total population of 10

Analysis:
- Very similar to cluster 0, but no harbours.
- Also almost no inhabitants, almost no income.
- Venues include mostly snack places and leasure zones
See also map and area names: industrial area

Conclusion:

Cluster is industrial area. Not suited for settling our salad bar

### Conclusion on cluster analysis

Best candidates for opening our salad bar are clusters 2 and 3. Both have presence of many other restaurants attract people to our restaurant.
We chose cluster 3 as the percentage of single person households is much higher, also average income is slightly higher.

### Potental competing salad bars already present

Now we try to select these postal codes in cluster 2 where no (or at least not that many) other salad bars are present.

In [113]:
#Create dataframe from only cluster 3
cluster3 = pcdata.loc[pcdata['cluster'] == 3]
cluster3.head()

postcode  cluster                     wijk               buurt woonplaats  \
0      1011        3       Nieuwmarkt/Lastage    Oosterdokseiland  Amsterdam   
1      1012        3  Burgwallen-Nieuwe Zijde  Stationsplein e.o.  Amsterdam   
2      1013        3          Haarlemmerbuurt    Westerdokseiland  Amsterdam   
3      1014        3    Westelijk Havengebied       Alfa-driehoek  Amsterdam   
4      1015        3      Grachtengordel-West    Langestraat e.o.  Amsterdam   

    gemeente      provincie   latitude  longitude  tot_inwoners   tot_0-5  \
0  Amsterdam  Noord-Holland  52.372976   4.903957        9605.0  0.030713   
1  Amsterdam  Noord-Holland  52.373386   4.894064        8245.0  0.026683   
2  Amsterdam  Noord-Holland  52.396789   4.876607       21185.0  0.052396   
3  Amsterdam  Noord-Holland  52.392305   4.855884         580.0  0.051724   
4  Amsterdam  Noord-Holland  52.379093   4.885109       14860.0  0.038694   

   tot_5-10  tot_10-15  tot_15-20  tot_20-25  tot_25-30  tot_30-35  tot_35-40  \
0  0.030193   0.022905   0.032795   0.092140   0.114524   0.086934   0.067673   
1  0.016374   0.013948   0.019406   0.133414   0.206792   0.141298   0.084900   
2  0.040359   0.031862   0.032570   0.060892   0.097947   0.101251   0.090158   
3  0.025862   0.008621   0.025862   0.043103   0.232759   0.215517   0.103448   
4  0.031292   0.028937   0.029946   0.073015   0.108008   0.097241   0.074361   

   tot_40-45  tot_45-50  tot_50-55  tot_55-60  tot_60-65  tot_65-70  \
0   0.064029   0.067673   0.080167   0.081728   0.078084   0.069755   
1   0.066101   0.061856   0.059430   0.050940   0.040631   0.036386   
2   0.078829   0.079537   0.076941   0.069389   0.063016   0.053576   
3   0.086207   0.060345   0.043103   0.043103   0.025862   0.017241   
4   0.072342   0.083109   0.079071   0.068977   0.062248   0.070996   

   tot_70-75  tot_75-80  tot_80-85  tot_85-90  tot_90-95   tot_95-   tot_man  \
0   0.037480   0.020822   0.011973   0.006247   0.003644  0.001562  0.519521   
1   0.021831   0.010309   0.004851   0.001819   0.000606  0.000000  0.545179   
2   0.031626   0.018881   0.012037   0.005664   0.002360  0.000708  0.501770   
3   0.017241   0.017241   0.008621   0.000000   0.000000  0.000000  0.577586   
4   0.038022   0.024226   0.012113   0.004711   0.002355  0.000336  0.506729   

    man_0-5  man_5-10  man_10-15  man_15-20  man_20-25  man_25-30  man_30-35  \
0  0.015096  0.014055   0.010932   0.015617   0.038522   0.053618   0.045809   
1  0.012735  0.007277   0.007277   0.007884   0.055791   0.102486   0.078229   
2  0.025490  0.021005   0.016285   0.016757   0.027614   0.044843   0.050979   
3  0.025862  0.008621   0.000000   0.017241   0.025862   0.129310   0.120690   
4  0.019179  0.015478   0.014805   0.015141   0.030283   0.049125   0.048789   

   man_35-40  man_40-45  man_45-50  man_50-55  man_55-60  man_60-65  \
0   0.039563   0.036960   0.040083   0.047892   0.044768   0.042686   
1   0.053366   0.043663   0.038205   0.040631   0.032747   0.023651   
2   0.043899   0.042011   0.043191   0.041539   0.034930   0.031626   
3   0.060345   0.060345   0.034483   0.034483   0.034483   0.017241   
4   0.039704   0.039031   0.045087   0.043742   0.037685   0.031629   

   man_65-70  man_70-75  man_75-80  man_80-85  man_85-90  man_90-95   man_95-  \
0   0.036439   0.019781   0.010411   0.005206   0.001562   0.001041  0.000521   
1   0.020619   0.012735   0.006671   0.002426   0.000606   0.000606  0.000000   
2   0.027142   0.016521   0.009913   0.005664   0.001888   0.000708  0.000000   
3   0.008621   0.008621   0.008621   0.008621   0.000000   0.000000  0.000000   
4   0.036339   0.019852   0.012450   0.005047   0.001682   0.000673  0.000336   

   tot_vrouw  vrouw_0-5  vrouw_5-10  vrouw_10-15  vrouw_15-20  vrouw_20-25  \
0   0.480479   0.015617    0.015617     0.011973     0.016658     0.053618   
1   0.454215   0.014554    0.009096     0.007884     0.012129     0.078229   
2   0.498230   0.026906    0.019353

In [115]:
cluster3.shape

(86, 92)

In [89]:
#Create dataframe of all salad bars
salad = venues[venues['venue category'].str.contains('salad', case=False)]
salad

postcode   latitude  longitude         venue  venue latitude  \
224       1015  52.379093   4.885109           SLA       52.378842   
462       1017  52.364185   4.890775  Poké Perfect       52.363934   
1330      1071  52.353865   4.882311        Venkel       52.354470   
1391      1072  52.352201   4.890314        Venkel       52.354470   
1404      1072  52.352201   4.890314           SLA       52.353206   
1436      1072  52.352201   4.890314       Sushito       52.354765   
1482      1073  52.351928   4.896904           SLA       52.353206   
1524      1073  52.351928   4.896904       Sushito       52.354765   
1639      1075  52.353424   4.860667           SLA       52.354808   
2179      1102  52.313517   4.954779   Urban Salad       52.312950   
2294      2511  52.079086   4.319048     GreenBowl       52.080025   
2363      2511  52.079086   4.319048  Grab 'n bite       52.080716   

      venue longitude venue category  
224          4.885336    Salad Place  
462          4.885700    Salad Place  
1330         4.888156    Salad Place  
1391         4.888156    Salad Place  
1404         4.893825    Salad Place  
1436         4.893452    Salad Place  
1482         4.893825    Salad Place  
1524         4.893452    Salad Place  
1639         4.855141    Salad Place  
2179         4.949479    Salad Place  
2294         4.318513    Salad Place  
2363         4.318947    Salad Place

In [90]:
#Group salad dataframe by postcode
saladpclist = salad.postcode.unique()
saladpclist

array([1015, 1017, 1071, 1072, 1073, 1075, 1102, 2511])

In [116]:
#Drop all postal codes with salad bar from cluster 3

# Get names of indexes for which column postcode is in saladpclist
indexNames = cluster3[cluster3['postcode'].isin(saladpclist)].index

# Delete these row indexes from dataFrame
cluster3.drop(indexNames , inplace=True)

cluster3

postcode  cluster                          wijk  \
0        1011        3            Nieuwmarkt/Lastage   
1        1012        3       Burgwallen-Nieuwe Zijde   
2        1013        3               Haarlemmerbuurt   
3        1014        3         Westelijk Havengebied   
5        1016        3       Burgwallen-Nieuwe Zijde   
7        1018        3  Oostelijke Eilanden/Kadijken   
28       1051        3             Staatsliedenbuurt   
29       1052        3             Staatsliedenbuurt   
30       1053        3                 Da Costabuurt   
31       1054        3                Centrale Markt   
32       1055        3                      Landlust   
33       1056        3                      Landlust   
34       1057        3                 Hoofdweg e.o.   
35       1058        3               Overtoomse Veld   
36       1059        3                Westlandgracht   
39       1062        3               Overtoomse Veld   
50       1074        3                     Oude Pijp   
52       1076        3                  Stadionbuurt   
54       1078        3                Museumkwartier   
55       1079        3                  Scheldebuurt   
61       1091        3               Oosterparkbuurt   
62       1092        3               Oosterparkbuurt   
63       1093        3                   Dapperbuurt   
64       1094        3           Indische Buurt West   
65       1095        3   Zeeburgereiland/Nieuwe Diep   
66       1096        3              Omval/Overamstel   
67       1097        3              Omval/Overamstel   
73       1105        3          Amstel III/Bullewijk   
86       2512        3               Wijk 28 Centrum   
87       2513        3              Wijk 42 Ypenburg   
88       2514        3               Wijk 28 Centrum   
90       2516        3         Wijk 27 Stationsbuurt   
91       2517        3     Wijk 22 Zeeheldenkwartier   
92       2518        3     Wijk 22 Zeeheldenkwartier   
93       2521        3         Wijk 27 Stationsbuurt   
115      2561        3    Wijk 21 Regentessekwartier   
116      2562        3              Wijk 11 Duinoord   
117      2563        3              Wijk 11 Duinoord   
134      2593        3          Wijk 26 Bezuidenhout   
136      2595        3         Wijk 27 Stationsbuurt   
139      3011        3             Rotterdam Centrum   
140      3012        3             Rotterdam Centrum   
141      3013        3             Rotterdam Centrum   
143      3015        3             Rotterdam Centrum   
144      3016        3             Rotterdam Centrum   
145      3021        3             Rotterdam Centrum   
148      3024        3                    Delfshaven   
152      3028        3                    Delfshaven   
154      3031        3           Kralingen-Crooswijk   
155      3032        3             Rotterdam Centrum   
156      3033        3                         Noord   
158      3035        3                         Noord   
161      3038        3                         Noord   
162      3039        3             Rotterdam Centrum   
176      3061        3           Kralingen-Crooswijk   
178      3063        3           Kralingen-Crooswijk   
196      3083        3                    Feijenoord   
203      3511        3            Wijk 06 Binnenstad   
204      3512        3            Wijk 06 Binnenstad   
205      3513        3            Wijk 06 Binnenstad   
206      3514        3             Wijk 04 Noordoost   
207      3515        3             Wijk 04 Noordoost   
208      3521        3            Wijk 06 Binnenstad   
209      3522        3              Wijk 08 Zuidwest   
210      3523        3                  Wijk 07 Zuid   
211      3524        3                  Wijk 07 Zuid   
213      3526        3              Wijk 08 Zuidwest   
216      3531        3            Wijk 06 Binnenstad   
217      3532        3                  Wijk 01 West   
225      3551        3             Wijk 02 Noordwest   
226      3552        3       

In [117]:
cluster3.shape

(80, 92)

So that does not help to bring selection much down, only 6 less. But good news, not that many salad bars in the selected cluster.

### Selecting postal code with highest percentage of females

In [120]:
select = cluster3.loc[cluster3.tot_vrouw.idxmax(axis = 0), :]
select

postcode                                  3572
cluster                                      3
wijk                         Wijk 04 Noordoost
buurt                            Tuinwijk-Oost
woonplaats                             Utrecht
gemeente                               Utrecht
provincie                              Utrecht
latitude                               52.0995
longitude                              5.13603
tot_inwoners                             11760
tot_0-5                              0.0590986
tot_5-10                              0.042517
tot_10-15                            0.0416667
tot_15-20                            0.0493197
tot_20-25                             0.134779
tot_25-30                             0.132653
tot_30-35                            0.0994898
tot_35-40                            0.0714286
tot_40-45                            0.0633503
tot_45-50                            0.0616497
tot_50-55                            0.0556973
tot_55-60    

<b>So, we have a winner it seems: postal code <u>3572</u></b>.

Lets do a final check on Foursquare if really no salad bar is close. As we obtained only 100 venues per postal code as maximum, we could have missed one.

In [141]:
#Build Foursquare statement
search_query = 'Salad'
latitude = select.latitude
longitude = select.longitude
radius = 500
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)

#Get results from Foursquare
results = requests.get(url).json()

# assign relevant part of JSON to venues
venueselect = results['response']['venues']

# tranform venues into a dataframe
venueselect = json_normalize(venueselect)
venueselect

Empty DataFrame
Columns: []
Index: []

In [127]:
venueselect.shape

(0, 0)

Dataframe is empty! So no competition it seems. Mission finding optimal postal code accomplished.

### Show map of winning postal code, with venues in winning postcal code plotted

In [137]:
#Obtain venues of winning postal code
winningvenues = venues[venues.postcode == select.postcode]
winningvenues

postcode   latitude  longitude                        venue  \
5152      3572  52.099466   5.136028               Roberto Gelato   
5153      3572  52.099466   5.136028          Restaurant C'est Ca   
5154      3572  52.099466   5.136028                     Goesting   
5155      3572  52.099466   5.136028     Grieks Restaurant Europa   
5156      3572  52.099466   5.136028                Gastmaal café   
5157      3572  52.099466   5.136028              Hans Snack Shop   
5158      3572  52.099466   5.136028  Zimihc Theater Wittevrouwen   
5159      3572  52.099466   5.136028                       Europa   
5160      3572  52.099466   5.136028                      De Kust   
5161      3572  52.099466   5.136028    Proost! Restaurant & Café   
5162      3572  52.099466   5.136028     Theaterhuis De Berenkuil   
5163      3572  52.099466   5.136028              Het Gouden Glas   
5164      3572  52.099466   5.136028          De Utrechtse Spelen   
5165      3572  52.099466   5.136028         De Paardenkathedraal   
5166      3572  52.099466   5.136028          Hotel Oorsprongpark   
5167      3572  52.099466   5.136028                  De Admiraal   
5168      3572  52.099466   5.136028         Bushalte Eykmanplein   
5169      3572  52.099466   5.136028             Tabakszaak Vroon   
5170      3572  52.099466   5.136028                     Soen Wah   
5171      3572  52.099466   5.136028                  Mangi Amore   
5172      3572  52.099466   5.136028           Van Everdingenlaan   
5173      3572  52.099466   5.136028              Blauwkapelseweg   
5174      3572  52.099466   5.136028      Cafetaria Oorsprongpark   
5175      3572  52.099466   5.136028             Slee Buitensport   
5176      3572  52.099466   5.136028         Gastmaal en de Tafel   
5177      3572  52.099466   5.136028          Brazilian Wax Salon   
5178      3572  52.099466   5.136028  Spoorwegovergang Biltstraat   

      venue latitude  venue longitude        venue category  
5152       52.098849         5.136149        Ice Cream Shop  
5153       52.098876         5.135154     French Restaurant  
5154       52.098585         5.137369     French Restaurant  
5155       52.097883         5.132560      Greek Restaurant  
5156       52.099062         5.129221                   Bar  
5157       52.098647         5.130232           Snack Place  
5158       52.096743         5.132302               Theater  
5159       52.097847         5.132535      Greek Restaurant  
5160       52.095702         5.138519     French Restaurant  
5161       52.099561         5.129223            Restaurant  
5162       52.095645         5.135994               Theater  
5163       52.098477         5.136775             Wine Shop  
5164       52.100028         5.134005               Theater  
5165       52.097735         5.137649               Theater  
5166       52.096204         5.138443       Bed & Breakfast  
5167       52.100033         5.139296                 Hotel  
5168       52.101122         5.133159              Bus Stop  
5169       52.102047         5.136468            Smoke Shop  
5170       52.096863         5.134065  Fast Food Restaurant  
5171       52.102340         5.136116    Italian Restaurant  
5172       52.102639         5.136130           Bus Station  
5173       52.098926         5.130561           Pizza Place  
5174       52.095938         5.138476  Fast Food Restaurant  
5175       52.095498         5.135927   Sporting Goods Shop  
5176       52.098910         5.129570         Deli / Bodega  
5177       52.098577         5.129020    Salon / Barbershop  
5178       52.095652         5.139613          Intersection

In [139]:
#Startpoint of map
winning_map = folium.Map(location=[latitude, longitude], zoom_start=16)

#Add area markers for each venue in file
for lat, lng, name, category in zip(winningvenues['venue latitude'], winningvenues['venue longitude'], winningvenues['venue'],
                                    winningvenues['venue category']):
    label = folium.Popup(str(category) + ': ' + str(name), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(winning_map)  

# display map
winning_map